### Initial imports

In [1]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import Imputer
from sklearn.neighbors import KNeighborsClassifier
from sklearn import metrics
from sklearn.svm import SVC
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.naive_bayes import GaussianNB
import pandas as pd
import numpy as np
import os
import re
from dateutil.relativedelta import relativedelta
from statsmodels.tsa import seasonal
from matplotlib import pyplot as plt
from functools import reduce  # Operação de reduce para cálculo de média de uma lista
from datetime import datetime
import math
%matplotlib inline

#Configurações para exibição de tableas
pd.set_option('display.height', 1000)
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)



/Users/Tiago/Library/Python/3.6/lib/python/site-packages/statsmodels/compat/pandas.py:56: FutureWarning: The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.
  from pandas.core import datetools


height has been deprecated.



### Auxiliary functions

In [2]:
# Nomes das colunas adicionadas ao dataframe
COLUNA_ANOMALIA_ACUMULADA = "anomalia_acumulada"
COLUNA_ANOMALIA_DO_MES = "anomalia_mensal"
COLUNA_MEDIA_MENSAL = "media_mensal"

# Todo mês possui 25 linhas por 38 colunas que dá 950
BLOCO_DE_DADOS_DE_UM_MES = 950
QUANTIDADE_DE_VALORES_DO_ARQUIVO = 573800  # (950 blocos x 604 meses,01/1964 até 04/2014)

class LatitudeColumns:

    def __init__(self):
        self.values = range(29, -21, -2)
        self.positive = 'N'
        self.negative = 'S'

    def get_all_columns(self):
        colum_names = []
        for value in self.values:
            if value > 0:
                colum_name = str(value) + self.positive
            else:
                colum_name = str(value) + self.negative
            colum_names.append(colum_name)
        return colum_names

    def get_single_column(self, desired_value, human_readable=True):
        sub_values = []
        for value in self.values:
            if value != desired_value:
                continue
            sub_values.append(value)
        if human_readable:
            return self.parse_human_readable(sub_values)
        return sub_values

    def get_range(self, init, final, human_readable=True):
        final, init = self.switch(final, init)

        sub_values = []
        if init == final:
            return self.get_single_column(init, human_readable)

        for value in self.values:
            if (value > init) or (value < final):
                continue
            sub_values.append(value)

        if human_readable:
            return self.parse_human_readable(sub_values)

        return sub_values

    def switch(self, final, init):
        if final > init:
            aux = init
            init = final
            final = aux
        return final, init

    def parse_human_readable(self, list):
        colum_names = []
        for value in list:
            if value > 0:
                colum_name = str(value) + self.positive
            else:
                colum_name = str(-value) + self.negative
            colum_names.append(colum_name)
        return colum_names

class LongitudeColumns:

    def __init__(self):
        #From map 60W to 15E(-17 because 'force' go to -15)
        self.values = range(59, -17, -2)
        self.positive = 'W'
        self.negative = 'E'

    def get_all_columns(self):
        colum_names = []
        for value in self.values:
            if value > 0:
                colum_name = str(value) + self.positive
            else:
                colum_name = str(value) + self.negative
            colum_names.append(colum_name)
        return colum_names

    def get_single_column(self, desired_value, human_readable=True):
        sub_values = []
        for value in self.values:
            if value != desired_value:
                continue
            sub_values.append(value)
        if human_readable:
            return self.parse_human_readable(sub_values)
        return sub_values

    def get_range(self, init, final, human_readable=True):
        final, init = self.switch(final, init)

        sub_values = []
        if init == final:
            return self.get_single_column(init, human_readable)

        for value in self.values:
            if (value > init) or (value < final):
                continue
            sub_values.append(value)

        if human_readable:
            return self.parse_human_readable(sub_values)

        return sub_values

    def switch(self, final, init):
        if final > init:
            aux = init
            init = final
            final = aux
        return final, init

    def parse_human_readable(self, list):
        colum_names = []
        for value in list:
            if value > 0:
                colum_name = str(value) + self.positive
            else:
                colum_name = str(-value) + self.negative
            colum_names.append(colum_name)
        return colum_names


def constroi_colunas_latitude_longitude(init_lat=29, end_lat=-21,
                                        init_long=59, end_long=-17):
    lat = LatitudeColumns().get_range(init_lat, end_lat)
    long = LongitudeColumns().get_range(init_long, end_long)
    colunas_do_data_frame = []
    for linha in lat:
        for coluna in long:
            lat_long = linha + "-" + coluna
            colunas_do_data_frame.append(lat_long)
    return colunas_do_data_frame


def carrega_array_com_valores_do_arquivo_geral(
        arquivo_com_decadas_de_anomalia="funceme_db/anomalia_tsm/geral/_Dados_TSMvento_2014_04_anomt6414b04"):
    global QUANTIDADE_DE_VALORES_DO_ARQUIVO

    conteudo_do_arquivo = open(arquivo_com_decadas_de_anomalia).read()
    conteudo_do_arquivo = conteudo_do_arquivo.replace("\n", "")

    # Carrega todos os dados de anomalia em um único array
    qtd_char_no_arquivo = 5
    # Todos os valores do arquivo em um único array. Não há separação de mês. Tudo está de forma sequencial
    valores_do_arquivo = []
    for rows_index in range(QUANTIDADE_DE_VALORES_DO_ARQUIVO):
        # slice data like (n:n+5)
        value = float(conteudo_do_arquivo[
                      rows_index * qtd_char_no_arquivo: rows_index * qtd_char_no_arquivo + qtd_char_no_arquivo])
        value = float("%.3f" % value)
        value /= 10
        valores_do_arquivo.append(value)
    return valores_do_arquivo


def carrega_array_com_valores_do_arquivo_mensal(file_name):
    file_content = open(file_name).read()

    # Remove header de um único arquivo
    file_content = file_content[25:]
    file_content = file_content.replace("\n", "")

    block_size = 5
    dados_do_arquivo = []
    for rows_index in range(BLOCO_DE_DADOS_DE_UM_MES):
        # slice data like (n:n+5)
        value = float(file_content[rows_index * block_size: rows_index * block_size + block_size])
        value = float("%.3f" % value)
        value /= 10
        dados_do_arquivo.append(value)

    return dados_do_arquivo


def merge_dados_do_diretorio(diretorio_arquivo_geral,diretorio_arquivo_individual):
    global QUANTIDADE_DE_VALORES_DO_ARQUIVO
    qtde = QUANTIDADE_DE_VALORES_DO_ARQUIVO
    lista_de_arquivos_individuais = []
    arquivos_do_diretorio = os.listdir(diretorio_arquivo_individual)

    quantidade_de_arquivos = 0
    # Adiciona apenas arquivos com extensão .22
    for arquivo in arquivos_do_diretorio:
        if arquivo.endswith(".22"):
            lista_de_arquivos_individuais.append(arquivo)
            quantidade_de_arquivos += 1

    valores_dos_arquivos = carrega_array_com_valores_do_arquivo_geral(diretorio_arquivo_geral)
    # Para cada arquivo na lista é feito append na lista full_data
    for arquivo in lista_de_arquivos_individuais:
        dados_mensais = carrega_array_com_valores_do_arquivo_mensal(diretorio_arquivo_individual + arquivo)
        for item in dados_mensais:
            valores_dos_arquivos.append(item)

    ##44 meses de 05/2014 até 12/2017
    qtde += quantidade_de_arquivos * BLOCO_DE_DADOS_DE_UM_MES  # Que dá 41800

    array_de_anomalias_por_mes = []
    for i in range(0, qtde, 950):
        anomalias_do_mes = valores_dos_arquivos[i:i + BLOCO_DE_DADOS_DE_UM_MES]
        array_de_anomalias_por_mes.append(anomalias_do_mes)
    return array_de_anomalias_por_mes


def inicia_funceme_data_frame(array_de_anomalias_por_mes):
    funceme_rainy_df = pd.DataFrame()
    for anomalias_do_mes in array_de_anomalias_por_mes:
        data = np.array(anomalias_do_mes)
        row_df = pd.DataFrame(data.reshape(-1, len(data)), columns=constroi_colunas_latitude_longitude())
        funceme_rainy_df = funceme_rainy_df.append(row_df)
    funceme_rainy_df.index = range(0, len(array_de_anomalias_por_mes), 1)
    # ### Setando indices baseados na data
    FORMAT = "%Y-%m"
    some_date_time1 = "1964-01"
    data_inicial = datetime.strptime(some_date_time1, FORMAT)
    indexes_data = []
    for i in range(len(array_de_anomalias_por_mes)):
        indexes_data.append(data_inicial + relativedelta(months=i))
    funceme_rainy_df = funceme_rainy_df.set_index(pd.DatetimeIndex(data=indexes_data))
    
    return funceme_rainy_df

def plota_coluna_do_dataframe(dataframe,titulo, nome_da_coluna, save_figure=False):
    fig, axarr = plt.subplots(1)
    fig.set_size_inches(8, 5)
    ax=dataframe[nome_da_coluna].plot( color='b', linestyle='-', grid=True)
    ax.set(xlabel="Year", ylabel="Celsius/10")

    plt.title(titulo)
    plt.tight_layout(pad=0.4, w_pad=0.5, h_pad=2.0)
    plt.axhline(0, color='black')
    if save_figure:
        plt.savefig("Imagens/tsm/"+titulo)
    else:        
        plt.show()
    
    plt.close()

def adiciona_media_mensal(dataframe):
    # Cria média para cada mês adicionando a coluna "media_mensal"
    media_da_figura_no_mes = []

    for date, row in dataframe.iterrows():
        media = (reduce(lambda x, y: x + y, row) / len(row))
        media_da_figura_no_mes.append(media)

    # Cria nova coluna chamada media_mensal e adiciona ao dataframe da funceme(funceme_rainy_df)
    dataframe.loc[:, "%s" % COLUNA_MEDIA_MENSAL] = pd.Series(media_da_figura_no_mes, index=dataframe.index)
    return dataframe

def calcula_climatologia_para_dataframe(dataframe):
    # Cria dicionário de médias anuais
    medias_anuais = {}
    for mes in range(1, 13, 1):
        medias_anuais[mes] = []

    for date, row in dataframe.iterrows():
        data = datetime.strptime(str(date), '%Y-%m-%d %H:%M:%S')
        medias_anuais[data.month].append(row[('%s' % COLUNA_MEDIA_MENSAL)])

    # Calcula climatologia para cada mês
    climatologias_mensais = {}
    for mes in range(1, 13, 1):
        climatologias_mensais[mes] = reduce(lambda x, y: x + y, medias_anuais[mes]) / len(medias_anuais[mes])
    return climatologias_mensais

def adiciona_anomalia(dataframe):
    climatologias_mensais = calcula_climatologia_para_dataframe(dataframe)

    ### Calculando anomalias
    anomalia = []
    for date, row in dataframe.iterrows():
        data = datetime.strptime(str(date), '%Y-%m-%d %H:%M:%S')
        anomalia_do_mes = row[COLUNA_MEDIA_MENSAL] - climatologias_mensais[data.month]
        anomalia.append(anomalia_do_mes)
    dataframe.loc[:, COLUNA_ANOMALIA_DO_MES] = pd.Series(anomalia, index=dataframe.index)
    dataframe.head(2)
    return dataframe

def adiciona_anomalia_acumulada(dataframe):
    anomalia_acumulada = []
    # Calcula anomalia acumulada
    for index in range(len(dataframe.index)):
        if index == 0:
            anomalia_acumulada.append(dataframe.iloc[index][COLUNA_ANOMALIA_DO_MES])
            continue
        anterior = anomalia_acumulada[index-1]
        atual = dataframe.iloc[index][COLUNA_ANOMALIA_DO_MES]
        anomalia_acumulada.append(float("%.3f" % (atual+anterior)))

    dataframe.loc[:, COLUNA_ANOMALIA_ACUMULADA] = pd.Series(anomalia_acumulada, index=dataframe.index)
    return dataframe

# Analisys starts from here

## Rainfall data from FUNCEME - Scraped since 1973

In [3]:
funceme_rainy_df = pd.read_csv("scraping/funceme_media_macrorregiao.csv", index_col=0 ,parse_dates=['datahora'])
media_observado_a_substituir = funceme_rainy_df.loc['1973-08-01 12:00:00']['Observado(mm)'].mean()
media_desvio_a_substituir = funceme_rainy_df.loc['1973-08-01 12:00:00']['Desvio(%)'].mean()

#Trata missing number
funceme_rainy_df['Normal(mm)'].fillna(media_observado_a_substituir, inplace=True)
funceme_rainy_df['Observado(mm)'].fillna(media_observado_a_substituir, inplace=True)
funceme_rainy_df['Desvio(%)'].fillna(media_desvio_a_substituir, inplace=True)

#Obtém média para cada coluna dos dados pluviométricos
medias = []
observado = []
desvio = []
for indices_unicos in funceme_rainy_df.index.unique():
    medias.append(funceme_rainy_df.loc[indices_unicos]['Normal(mm)'].mean())
    observado.append(funceme_rainy_df.loc[indices_unicos]['Observado(mm)'].mean())
    desvio.append(funceme_rainy_df.loc[indices_unicos]['Desvio(%)'].mean())

    #Cria novo Pandas Dataframe
funceme_rainy_montlhy_df = pd.DataFrame(index=funceme_rainy_df.index.unique().tolist())

#Adiciona dados mensais do estado ao Dataframe criado
funceme_rainy_montlhy_df = pd.concat(
    [funceme_rainy_montlhy_df, 
        pd.DataFrame(data=medias, index=funceme_rainy_montlhy_df.index, columns= ['Normal(mm)']),
        pd.DataFrame(data=observado, index=funceme_rainy_montlhy_df.index, columns= ['Observado(mm)']),
        pd.DataFrame(data=desvio, index=funceme_rainy_montlhy_df.index, columns= ['Desvio(%)'])],
    axis=1, join_axes=[funceme_rainy_montlhy_df.index])
funceme_rainy_montlhy_df.head()

##Set values to class
rainy_seasonal_months = [2,3,4] #February, March, April

indexes = []
rows = []

for index,row in funceme_rainy_montlhy_df.iterrows():
    if index.month not in rainy_seasonal_months:
        continue
    indexes.append(index)
    rows.append(row)

rainy_classified_df = pd.DataFrame(index=indexes, columns=funceme_rainy_montlhy_df.columns,data=rows)

rainy_classified_df = rainy_classified_df.groupby(rainy_classified_df.index.year).mean()

strong = 'strong'
normal = 'normal'
weak = 'weak'

classes = []

for index, row in rainy_classified_df.iterrows():
#     print(index)
    if row['Observado(mm)'] < 200:
        classes.append(weak)
        continue
    
    if row['Observado(mm)'] < 300:
        classes.append(normal)
        continue
        
    classes.append(strong)
rainy_classified_df['classes'] = classes
rainy_classified_df = rainy_classified_df['classes']
rainy_classified_df.head(5)

1973    normal
1974    strong
1975    normal
1976      weak
1977      weak
Name: classes, dtype: object

## Filter SST anomaly from 1973

In [4]:
array_de_anomalias_por_mes = merge_dados_do_diretorio("funceme_db/tsm/geral/_Dados_TSMvento_2014_04_sst6414b04","funceme_db/anomalia_tsm/individual/")
geral_df = inicia_funceme_data_frame(array_de_anomalias_por_mes)
funceme_sst_df = geral_df.loc['1973-01-01':'2017-12-01']
funceme_sst_df = funceme_sst_df.replace(9999.8, np.nan)
funceme_sst_df = funceme_sst_df.dropna(axis=1, how='any')

# Probably won`t use it
# funceme_sst_df = adiciona_media_mensal(funceme_sst_df)
# funceme_sst_df = adiciona_anomalia(funceme_sst_df)
# funceme_sst_df = adiciona_anomalia_acumulada(funceme_sst_df)

## Remove first semester from SST dataframe

In [5]:
second_semester_months=[7,8,9,10,11,12] # From August to December


In [6]:
indexes = []
rows = []

for index,row in funceme_sst_df.iterrows():
    if index.month not in second_semester_months:
        continue
    indexes.append(index)
    rows.append(row)

sst_full_area_jul_dez_df = pd.DataFrame(index=indexes, columns=funceme_sst_df.columns,data=rows)
sst_full_area_jul_dez_df.head(3)

29N-59W  29N-57W  29N-55W  29N-53W  29N-51W  29N-49W  29N-47W  29N-45W  29N-43W  29N-41W  29N-39W  29N-37W  29N-35W  29N-33W  29N-31W  29N-29W  29N-27W  29N-25W  29N-23W  29N-21W  29N-19W  29N-17W  29N-15W  29N-13W  27N-59W  27N-57W  27N-55W  27N-53W  27N-51W  27N-49W  27N-47W  27N-45W  27N-43W  27N-41W  27N-39W  27N-37W  27N-35W  27N-33W  27N-31W  27N-29W  27N-27W  27N-25W  27N-23W  27N-21W  27N-19W  27N-17W  27N-15W  25N-59W  25N-57W  25N-55W  25N-53W  25N-51W  25N-49W  25N-47W  25N-45W  25N-43W  25N-41W  25N-39W  25N-37W  25N-35W  25N-33W  25N-31W  25N-29W  25N-27W  25N-25W  25N-23W  25N-21W  25N-19W  25N-17W  25N-15W  23N-59W  23N-57W  23N-55W  23N-53W  23N-51W  23N-49W  23N-47W  23N-45W  23N-43W  23N-41W  23N-39W  23N-37W  23N-35W  23N-33W  23N-31W  23N-29W  23N-27W  23N-25W  23N-23W  23N-21W  23N-19W  23N-17W  21N-59W  21N-57W  21N-55W  21N-53W  21N-51W  21N-49W  21N-47W  21N-45W  21N-43W  21N-41W  21N-39W  21N-37W  21N-35W  21N-33W  21N-31W  21N-29W  21N-27W  \
1973-07-01     26.3     26.2     26.0     25.7     25.6     25.5     25.4     25.3     25.2     25.1     24.7     24.3     24.0     23.9     23.4     23.2     22.9     22.6     22.3     22.0     21.7     21.3     21.1     20.8     26.9     26.7     26.4     26.1     25.9     25.7     25.5     25.4     25.2     24.9     24.6     24.2     23.9     23.6     23.4     23.2     23.0     22.7     22.3     22.0     21.6     21.0     20.7     27.4     27.2     26.8     26.5     26.2     26.0     25.8     25.5     25.1     24.7     24.4     24.1     23.8     23.5     23.4     23.4     23.4     23.0     22.4     21.9     21.1     20.3     19.7     27.6     27.4     27.2     26.8     26.5     26.3     26.1     25.6     25.2     24.7     24.5     24.1     23.8     23.6     23.6     23.7     23.6     23.2     22.6     21.7     20.6     19.5     27.8     27.6     27.3     27.0     26.8     26.5     26.1     25.7     25.3     25.0     24.7     24.4     24.1     23.9     23.9     23.8     23.7   
1973-08-01     27.7     27.6     27.5     27.2     27.0     26.7     26.5     26.3     26.2     25.8     25.4     25.2     24.9     24.8     24.5     24.1     23.7     23.4     23.1     22.8     22.3     21.7     21.3     20.9     27.8     27.7     27.4     27.1     26.9     26.6     26.3     26.1     25.9     25.5     25.2     24.9     24.6     24.2     24.0     23.8     23.5     23.3     23.1     22.6     22.0     21.3     20.8     27.7     27.6     27.4     27.1     26.8     26.5     26.3     26.0     25.6     25.3     25.0     24.8     24.3     23.8     23.5     23.4     23.3     23.3     23.0     22.5     21.4     20.4     20.0     27.7     27.6     27.4     27.2     26.9     26.7     26.4     26.0     25.5     25.3     25.1     24.8     24.3     23.8     23.4     23.3     23.2     23.4     23.3     22.5     21.2     19.8     27.7     27.6     27.5     27.3     27.1     26.9     26.5     26.2     25.8     25.4     25.2     24.9     24.6     24.4     24.0     23.7     23.6   
1973-09-01     28.2     28.0     27.8     27.6     27.3     27.1     27.0     26.9     26.8     26.7     26.5     26.2     25.8     25.5     25.2     25.1     24.8     24.3     23.6     23.0     22.8     22.6     22.2     21.7     28.3     28.1     27.8     27.5     27.2     27.1     26.9     26.7     26.6     26.4     26.1     25.8     25.6     25.3     25.1     25.0     24.7     24.3     23.7     23.1     22.6     22.0     21.5     28.2     28.0     27.7     27.4     27.1     26.9     26.8     26.6     26.3     26.0     25.8     25.5     25.3     24.9     24.8     24.9     24.7     24.4     23.9     23.1     22.0     20.9     20.1     28.0     27.8     27.6     27.3     27.0     26.9     26.8     26.5     26.2     26.0     25.8     25.5     25.1     24.8     24.7     24.6     24.6     24.6     24.1     23.1     21.6     20.0     27.8     27.7     27.5     27.3     27.1     27.0     26.8     26.7     26.5     26.4     26.2     25.9     25.5     25.0     24.6     24.6     24.7   

            21N-25W  21N-23W  2

## Creating transformed df from SST full area

In [7]:
def create_transformed_df(dataframe, column_name_prefix, initial_year = 1973, end_year=2018):
    columns = dataframe.columns 
    months = second_semester_months
    merged_colum_names=[]
    

    for col in columns:
        for month in months:
            column_name = column_name_prefix + col + '_' +str(month)
            merged_colum_names.append(column_name)
            
    dataframe_transformed_df = pd.DataFrame(index=range(1973,2018,1), columns=merged_colum_names)
    
    for year in range(initial_year, end_year, 1):
    #     print("Year " , year) # FOR DEBUG ONLY
        for month in range(7,13,1):
            for column_name in dataframe.columns:
                value = dataframe.loc[str(year)+'-'+str(month)+'-01'][column_name]
                column_name = column_name_prefix +column_name+'_'+str(month)
                dataframe_transformed_df.set_value(year, column_name, value)
    return dataframe_transformed_df

In [8]:
# columns = sst_full_area_jul_dez_df.columns 
# months = second_semester_months
# merged_colum_names=[]

# for col in columns:
#     for month in months:
#         column_name = 'sst_' + col + '_' +str(month)
#         merged_colum_names.append(column_name)

In [9]:
#For debugy only
# for column_name in merged_colum_names:
#     print(column_name)

In [10]:
# sst_transformed_df = pd.DataFrame(index=range(1973,2018,1), columns=merged_colum_names)

In [11]:
# for year in range(1973,2018,1):
#     #     print("Year " , year) # FOR DEBUG ONLY
#     for month in range(7,13,1):
#         for sst_column in sst_full_area_jul_dez_df.columns:
#             value = sst_full_area_jul_dez_df.loc[str(year)+'-'+str(month)+'-01'][sst_column]
#             column_name = 'sst_' +sst_column+'_'+str(month)
#             sst_transformed_df.set_value(year, column_name, value)
            

In [12]:
sst_transformed_df = create_transformed_df(sst_full_area_jul_dez_df, "sst_")

In [13]:
sst_transformed_df.head(3)

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
1973          26.3          27.7          28.2           26.5             25           22.3          26.2          27.6            28           26.4           24.9           22.2            26          27.5          27.8           26.2           24.7           22.1          25.7          27.2          27.6             26           24.5           22.1          25.6            27          27.3           25.9           24.4           22.1          25.5          26.7          27.1           25.8           24.4           22.2          25.4          26.5            27           25.7           24.4           22.3          25.3          26.3          26.9           25.7           24.4           22.3          25.2          26.2          26.8           25.7           24.4           22.2          25.1          25.8          26.7           25.6           24.2           22.3          24.7          25.4          26.5           25.4           23.8           22.4          24.3          25.2   
1974          27.1          27.4          27.4           25.9           24.7           22.8          26.8          27.4          27.4           25.9           24.7           22.9          26.5          27.2          27.2           25.9           24.6           22.9          26.1            27          27.1           25.8           24.5             23          26.1            27          26.9           25.8           24.4           22.9          26.2          26.9          26.8           25.7           24.2           22.7          26.2          26.7          26.5           25.5           24.1           22.6          25.6          26.3          25.9           25.3             24           22.5            25          25.9          25.3           25.1             24           22.5          24.5          25.5            25           24.8           24.1           22.4          24.2          25.5            25           24.7           24.1           22.2            24          25.3   
1975          26.4          27.8          28.2           26.7           25.3           22.5          26.4          27.8            28           26.7           25.2           22.5          26.3          27.8          27.9           26.7           25.1           22.5          26.3          27.7          27.6           26.6           24.9           22.4          26.4          27.6          27.3           26.3           24.8           22.3          26.4          27.4          27.1             26           24.6           22.2          26.3          27.3          26.9           25.6           24.4           22.1          25.9          27.1          26.7           25.3           24.1           21.9          25.5          26.9          26.5           25.1           23.9           21.9          25.3          26.6          26.5             25           23.6           21.8          25.1          26.4          26.4             25           23.4             22            25          26.2   

     sst_29N-37W_9 sst_29N-37W_1

In [14]:
sst_transformed_df.head(3)

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
1973          26.3          27.7          28.2           26.5             25           22.3          26.2          27.6            28           26.4           24.9           22.2            26          27.5          27.8           26.2           24.7           22.1          25.7          27.2          27.6             26           24.5           22.1          25.6            27          27.3           25.9           24.4           22.1          25.5          26.7          27.1           25.8           24.4           22.2          25.4          26.5            27           25.7           24.4           22.3          25.3          26.3          26.9           25.7           24.4           22.3          25.2          26.2          26.8           25.7           24.4           22.2          25.1          25.8          26.7           25.6           24.2           22.3          24.7          25.4          26.5           25.4           23.8           22.4          24.3          25.2   
1974          27.1          27.4          27.4           25.9           24.7           22.8          26.8          27.4          27.4           25.9           24.7           22.9          26.5          27.2          27.2           25.9           24.6           22.9          26.1            27          27.1           25.8           24.5             23          26.1            27          26.9           25.8           24.4           22.9          26.2          26.9          26.8           25.7           24.2           22.7          26.2          26.7          26.5           25.5           24.1           22.6          25.6          26.3          25.9           25.3             24           22.5            25          25.9          25.3           25.1             24           22.5          24.5          25.5            25           24.8           24.1           22.4          24.2          25.5            25           24.7           24.1           22.2            24          25.3   
1975          26.4          27.8          28.2           26.7           25.3           22.5          26.4          27.8            28           26.7           25.2           22.5          26.3          27.8          27.9           26.7           25.1           22.5          26.3          27.7          27.6           26.6           24.9           22.4          26.4          27.6          27.3           26.3           24.8           22.3          26.4          27.4          27.1             26           24.6           22.2          26.3          27.3          26.9           25.6           24.4           22.1          25.9          27.1          26.7           25.3           24.1           21.9          25.5          26.9          26.5           25.1           23.9           21.9          25.3          26.6          26.5             25           23.6           21.8          25.1          26.4          26.4             25           23.4             22            25          26.2   

     sst_29N-37W_9 sst_29N-37W_1

## PSW

In [15]:
array_dados_brutos_x = merge_dados_do_diretorio("funceme_db/pseudo_tensao_x_dados_brutos/geral/_Dados_TSMvento_2014_04_pwsx6414b04","funceme_db/pseudo_tensao_x_dados_brutos/individual/")
array_dados_brutos_y = merge_dados_do_diretorio("funceme_db/pseudo_tensao_y_dados_brutos/geral/_Dados_TSMvento_2014_04_pwsy6414b04","funceme_db/pseudo_tensao_y_dados_brutos/individual/")

In [16]:
#For debug only
#array_dados_brutos_x[0]

In [17]:
#For debug only
# array_dados_brutos_y[0]

In [18]:
pws = []
for month_index in range(len(array_dados_brutos_x)):
    scalar_product_list = []
    for value_index in range(len(array_dados_brutos_x[month_index])):
        scalar_product = math.sqrt(pow(array_dados_brutos_x[month_index][value_index],2) + pow(array_dados_brutos_y[month_index][value_index],2))
        if scalar_product == 14141.852781018475:
            scalar_product_list.append(np.nan)
        else:
            scalar_product_list.append(scalar_product)
    pws.append(scalar_product_list)

In [19]:
#For debug only
# pws[0][0]

In [20]:
#For debug only
# pws[0][1]

In [21]:
pws_full_area_df = inicia_funceme_data_frame(pws)
pws_full_area_df.head(3)

29N-59W    29N-57W    29N-55W    29N-53W    29N-51W    29N-49W    29N-47W    29N-45W    29N-43W    29N-41W    29N-39W    29N-37W    29N-35W    29N-33W    29N-31W    29N-29W    29N-27W    29N-25W    29N-23W    29N-21W    29N-19W    29N-17W    29N-15W    29N-13W  29N-11W  29N-9W  29N-7W  29N-5W  29N-3W  29N-1W  29N-1E  29N-3E  29N-5E  29N-7E  29N-9E  29N-11E  29N-13E  29N-15E   27N-59W    27N-57W    27N-55W    27N-53W    27N-51W    27N-49W    27N-47W    27N-45W    27N-43W    27N-41W    27N-39W    27N-37W    27N-35W    27N-33W    27N-31W    27N-29W    27N-27W    27N-25W    27N-23W    27N-21W    27N-19W    27N-17W    27N-15W  27N-13W  27N-11W  27N-9W  27N-7W  27N-5W  27N-3W  27N-1W  27N-1E  27N-3E  27N-5E  27N-7E  27N-9E  27N-11E  27N-13E  27N-15E    25N-59W    25N-57W    25N-55W    25N-53W    25N-51W    25N-49W   25N-47W   25N-45W   25N-43W   25N-41W   25N-39W    25N-37W    25N-35W    25N-33W    25N-31W    25N-29W    25N-27W    25N-25W    25N-23W    25N-21W    25N-19W  \
1964-01-01   0.632456  10.855874  16.995588  20.727035  22.036787  20.506097  15.060212  11.806778  13.165485  15.928905  18.720043  19.382982  19.275373  19.183847  18.293715  17.761194  18.120155  17.602557  13.476646   7.528612   4.560702   8.732125  11.524756  14.120906      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  3.244996  10.002000  15.212166  17.901117  18.740864  16.707483  11.780068   8.780091   9.323626  10.748023  12.103718  11.229426  10.733592  10.340696   9.818350  10.526158  10.160709   9.411164   5.622277   0.894427   6.016644   9.669023  11.300000      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN   8.043009  11.260551  14.524806  16.419501  16.800000  14.603082  9.377100  5.220153  3.894868  4.114608  4.414748   2.009975   0.721110   0.200000   4.254409  10.599057   9.757561   6.862215   5.745433   8.005623  12.615070   
1964-02-01  17.098538  17.184295  17.779201  17.861691  17.640011  16.752313  18.947559  21.159631  22.610838  24.200207  24.018743  22.314345  19.912308  17.994721  16.127616  14.400000  10.756393   7.930952   8.962700  15.041609  20.021239  16.942550  12.280065   5.546170      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  8.213404   9.700000  10.960383  11.395174  11.510864  11.067972  11.977479  13.050670  14.272001  14.632840  14.142136  11.524756  10.072239   8.956004   6.896376   5.597321   6.802941  10.024470  15.423683  20.821623  24.816930  23.452292  20.388722      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN   7.158911   5.724509   5.115662   4.805206   4.272002   2.828427  0.824621  1.513275  2.200000  3.201562  5.385165   6.711930   6.403124   7.481310   9.403191  12.452309  16.194135  19.586985  24.211774  27.960866  30.176315   
1964-03-01  11.531262  10.567876  10.404326   9.708244   9.749359  11.044003  15.101324  18.047160  23.809662  29.179616  33.301351  35.700560  36.693869  36.477390  35.288100  31.840226  27.049030  20.938959  16.902663  19.531001  25.536053  26.792723  25.656383  22.461077      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  2.000000   0.921954   1.772005   3.436568   5.008992   6.095900   7.051950   8.709191  11.374533  14.524806  17.507141  22.073740  25.448379  26.210113  25.504901  22.971286  18.363279  15.618579  19.406442  26.637192  32.747824  34.917761  34.197076      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  16.807439  17.719199  17.265283  15.171684  12.539936   9.577578  7.648529  6.438167  6.648308  6.220129  7.253275  12.800391  18.926437  22.065811  20.961870  17.791009  15.938005  18.626057  27.536340  36.815486  42.290661   

              25N-17W    

In [22]:
## Remove first semester from PWS dataframe

In [23]:
indexes = []
rows = []

for index,row in pws_full_area_df.iterrows():
    if index.month not in second_semester_months:
        continue
    indexes.append(index)
    rows.append(row)

pws_full_area_jul_dez_df = pd.DataFrame(index=indexes, columns=pws_full_area_df.columns,data=rows)


# TESTIN THIS CASE

In [24]:
pws_full_area_jul_dez_df.head(3)

29N-59W    29N-57W    29N-55W    29N-53W    29N-51W    29N-49W    29N-47W    29N-45W    29N-43W    29N-41W    29N-39W    29N-37W    29N-35W    29N-33W    29N-31W    29N-29W    29N-27W    29N-25W    29N-23W    29N-21W    29N-19W    29N-17W    29N-15W    29N-13W  29N-11W  29N-9W  29N-7W  29N-5W  29N-3W  29N-1W  29N-1E  29N-3E  29N-5E  29N-7E  29N-9E  29N-11E  29N-13E  29N-15E    27N-59W    27N-57W    27N-55W    27N-53W    27N-51W    27N-49W    27N-47W    27N-45W    27N-43W    27N-41W    27N-39W    27N-37W    27N-35W    27N-33W    27N-31W    27N-29W    27N-27W    27N-25W    27N-23W    27N-21W    27N-19W    27N-17W    27N-15W  27N-13W  27N-11W  27N-9W  27N-7W  27N-5W  27N-3W  27N-1W  27N-1E  27N-3E  27N-5E  27N-7E  27N-9E  27N-11E  27N-13E  27N-15E    25N-59W    25N-57W    25N-55W    25N-53W    25N-51W    25N-49W    25N-47W    25N-45W    25N-43W    25N-41W    25N-39W    25N-37W    25N-35W    25N-33W    25N-31W    25N-29W    25N-27W    25N-25W    25N-23W    25N-21W  \
1964-07-01  18.346934  16.812198  16.357261  15.190787  14.748898  14.500000  12.800391  13.613229  14.334922  17.593465  22.378785  28.579188  35.243297  44.715210  51.315690  58.789965  57.622305  55.833771  55.286979  59.052942  63.558556  64.111933  61.036137  54.658668      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  23.576471  23.433523  23.742788  23.436083  23.400855  23.568835  23.385679  24.758837  28.731342  33.217465  38.946373  45.060071  50.732632  56.257000  59.907679  61.729248  57.360003  54.223334  56.180513  61.494146  69.029342  71.331970  70.479075      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  31.533633  33.559648  34.628312  35.300142  35.445733  36.168633  37.561683  39.588382  45.743306  51.138342  56.981488  62.658200  65.836920  66.850580  67.544504  65.046599  58.033180  52.559014  55.822934  62.541186   
1964-08-01  11.520851   8.276473   6.280127   4.701064   4.001250   3.862642   3.605551   4.036087   3.935734   4.177320   4.850773   9.415413  13.917615  14.752627  12.747549   8.766413   2.024846   4.390900   9.347727  19.795201  30.372520  37.608510  40.351456  38.398568      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  11.322985  10.465180  10.235722   9.824968   9.219544   8.668333   8.572631   9.247702  10.751744  12.280065  13.036104  14.763468  17.962739  18.117671  15.241063  10.381233   6.688797   7.800000  15.980613  27.430275  38.417314  45.015553  47.416980      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  18.952572  19.630843  20.600000  20.319941  19.791412  18.642425  18.631693  20.130822  22.568341  23.764048  24.542209  26.442579  29.585300  29.329337  26.580068  20.972363  16.686821  16.681727  25.181342  36.850644   
1964-09-01  29.050473  25.904633  23.020860  20.615528  19.285487  19.543285  19.216659  18.003611  16.181780  15.415577  16.430460  24.253866  30.951090  35.517883  37.800132  38.213348  35.357036  32.829864  28.160433  23.924046  21.667026  22.517771  21.949487  20.106218      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  30.383219  27.906272  25.440322  24.066574  23.561409  23.810292  23.031283  21.440149  19.331322  18.013606  19.147062  24.440131  30.272925  35.403531  38.575122  39.012818  37.186019  34.839776  32.313619  30.619765  30.103986  30.384865  29.415982      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  32.339604  30.046630  28.438179  28.327019  28.876461  29.400170  28.385384  26.404734  23.843028  22.357325  23.090258  26.545244  32.345943  38.283286  42.406250  43.370266  42.370981  41.281957  40.205721  40.396658   

              25N-19W    25N-17W    25N-15W  

### Treating missing data

In [25]:
pws_full_area_jul_dez_df = pws_full_area_jul_dez_df.replace(14141.852781018475, np.nan)
pws_full_area_jul_dez_df.head(3)

29N-59W    29N-57W    29N-55W    29N-53W    29N-51W    29N-49W    29N-47W    29N-45W    29N-43W    29N-41W    29N-39W    29N-37W    29N-35W    29N-33W    29N-31W    29N-29W    29N-27W    29N-25W    29N-23W    29N-21W    29N-19W    29N-17W    29N-15W    29N-13W  29N-11W  29N-9W  29N-7W  29N-5W  29N-3W  29N-1W  29N-1E  29N-3E  29N-5E  29N-7E  29N-9E  29N-11E  29N-13E  29N-15E    27N-59W    27N-57W    27N-55W    27N-53W    27N-51W    27N-49W    27N-47W    27N-45W    27N-43W    27N-41W    27N-39W    27N-37W    27N-35W    27N-33W    27N-31W    27N-29W    27N-27W    27N-25W    27N-23W    27N-21W    27N-19W    27N-17W    27N-15W  27N-13W  27N-11W  27N-9W  27N-7W  27N-5W  27N-3W  27N-1W  27N-1E  27N-3E  27N-5E  27N-7E  27N-9E  27N-11E  27N-13E  27N-15E    25N-59W    25N-57W    25N-55W    25N-53W    25N-51W    25N-49W    25N-47W    25N-45W    25N-43W    25N-41W    25N-39W    25N-37W    25N-35W    25N-33W    25N-31W    25N-29W    25N-27W    25N-25W    25N-23W    25N-21W  \
1964-07-01  18.346934  16.812198  16.357261  15.190787  14.748898  14.500000  12.800391  13.613229  14.334922  17.593465  22.378785  28.579188  35.243297  44.715210  51.315690  58.789965  57.622305  55.833771  55.286979  59.052942  63.558556  64.111933  61.036137  54.658668      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  23.576471  23.433523  23.742788  23.436083  23.400855  23.568835  23.385679  24.758837  28.731342  33.217465  38.946373  45.060071  50.732632  56.257000  59.907679  61.729248  57.360003  54.223334  56.180513  61.494146  69.029342  71.331970  70.479075      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  31.533633  33.559648  34.628312  35.300142  35.445733  36.168633  37.561683  39.588382  45.743306  51.138342  56.981488  62.658200  65.836920  66.850580  67.544504  65.046599  58.033180  52.559014  55.822934  62.541186   
1964-08-01  11.520851   8.276473   6.280127   4.701064   4.001250   3.862642   3.605551   4.036087   3.935734   4.177320   4.850773   9.415413  13.917615  14.752627  12.747549   8.766413   2.024846   4.390900   9.347727  19.795201  30.372520  37.608510  40.351456  38.398568      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  11.322985  10.465180  10.235722   9.824968   9.219544   8.668333   8.572631   9.247702  10.751744  12.280065  13.036104  14.763468  17.962739  18.117671  15.241063  10.381233   6.688797   7.800000  15.980613  27.430275  38.417314  45.015553  47.416980      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  18.952572  19.630843  20.600000  20.319941  19.791412  18.642425  18.631693  20.130822  22.568341  23.764048  24.542209  26.442579  29.585300  29.329337  26.580068  20.972363  16.686821  16.681727  25.181342  36.850644   
1964-09-01  29.050473  25.904633  23.020860  20.615528  19.285487  19.543285  19.216659  18.003611  16.181780  15.415577  16.430460  24.253866  30.951090  35.517883  37.800132  38.213348  35.357036  32.829864  28.160433  23.924046  21.667026  22.517771  21.949487  20.106218      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  30.383219  27.906272  25.440322  24.066574  23.561409  23.810292  23.031283  21.440149  19.331322  18.013606  19.147062  24.440131  30.272925  35.403531  38.575122  39.012818  37.186019  34.839776  32.313619  30.619765  30.103986  30.384865  29.415982      NaN      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN      NaN      NaN      NaN  32.339604  30.046630  28.438179  28.327019  28.876461  29.400170  28.385384  26.404734  23.843028  22.357325  23.090258  26.545244  32.345943  38.283286  42.406250  43.370266  42.370981  41.281957  40.205721  40.396658   

              25N-19W    25N-17W    25N-15W  

In [26]:
pws_full_area_jul_dez_df = pws_full_area_jul_dez_df.dropna(axis=1, how='any')
pws_full_area_jul_dez_df.head(2)

29N-59W    29N-57W    29N-55W    29N-53W    29N-51W    29N-49W    29N-47W    29N-45W    29N-43W    29N-41W    29N-39W    29N-37W    29N-35W    29N-33W    29N-31W    29N-29W    29N-27W    29N-25W    29N-23W    29N-21W    29N-19W    29N-17W    29N-15W    29N-13W    27N-59W    27N-57W    27N-55W    27N-53W    27N-51W    27N-49W    27N-47W    27N-45W    27N-43W    27N-41W    27N-39W    27N-37W    27N-35W    27N-33W    27N-31W    27N-29W    27N-27W    27N-25W    27N-23W    27N-21W    27N-19W    27N-17W    27N-15W    25N-59W    25N-57W    25N-55W    25N-53W    25N-51W    25N-49W    25N-47W    25N-45W    25N-43W    25N-41W    25N-39W    25N-37W   25N-35W    25N-33W    25N-31W    25N-29W    25N-27W    25N-25W    25N-23W    25N-21W    25N-19W    25N-17W    25N-15W    23N-59W    23N-57W    23N-55W    23N-53W    23N-51W    23N-49W    23N-47W    23N-45W    23N-43W    23N-41W    23N-39W    23N-37W    23N-35W    23N-33W    23N-31W    23N-29W    23N-27W    23N-25W    23N-23W  \
1964-07-01  18.346934  16.812198  16.357261  15.190787  14.748898  14.500000  12.800391  13.613229  14.334922  17.593465  22.378785  28.579188  35.243297  44.715210  51.315690  58.789965  57.622305  55.833771  55.286979  59.052942  63.558556  64.111933  61.036137  54.658668  23.576471  23.433523  23.742788  23.436083  23.400855  23.568835  23.385679  24.758837  28.731342  33.217465  38.946373  45.060071  50.732632  56.257000  59.907679  61.729248  57.360003  54.223334  56.180513  61.494146  69.029342  71.331970  70.479075  31.533633  33.559648  34.628312  35.300142  35.445733  36.168633  37.561683  39.588382  45.743306  51.138342  56.981488  62.658200  65.83692  66.850580  67.544504  65.046599  58.033180  52.559014  55.822934  62.541186  71.157572  75.700264  78.930919  40.707862  43.601835  44.700112  45.508900  46.432101  48.027700  51.736641  54.282594  60.096589  66.296606  70.677083  73.594361  74.349714  72.782759  68.831533  65.816715  57.495130  50.806791  52.517807   
1964-08-01  11.520851   8.276473   6.280127   4.701064   4.001250   3.862642   3.605551   4.036087   3.935734   4.177320   4.850773   9.415413  13.917615  14.752627  12.747549   8.766413   2.024846   4.390900   9.347727  19.795201  30.372520  37.608510  40.351456  38.398568  11.322985  10.465180  10.235722   9.824968   9.219544   8.668333   8.572631   9.247702  10.751744  12.280065  13.036104  14.763468  17.962739  18.117671  15.241063  10.381233   6.688797   7.800000  15.980613  27.430275  38.417314  45.015553  47.416980  18.952572  19.630843  20.600000  20.319941  19.791412  18.642425  18.631693  20.130822  22.568341  23.764048  24.542209  26.442579  29.58530  29.329337  26.580068  20.972363  16.686821  16.681727  25.181342  36.850644  47.594643  53.791914  56.668157  31.100643  32.695718  33.833268  33.543554  33.353860  33.328966  34.491158  35.146124  35.521824  36.497123  37.481329  40.534553  43.982951  44.864240  42.283448  36.752823  30.871508  27.895878  33.677441   

              23N-21W    23N-19W    23N-17W    21N-59W    21N-57W    21N-55W    21N-53W    21N-51W    21N-49W    21N-47W    21N-45W    21N-43W    21N-41W    21N-39W    21N-37W    21N-35W    21N-33W    21N-31W    21N-29W    21N-27W    21N-25W    21N-23W    21N-21W    21N-19W    21N-17W    19N-59W    19N-57W    19N-55W    19N-53W    19N-51W    19N-49W    19N-47W    19N-45W    19N-43W    19N-41W    19N-39W    19N-37W    19N-35W    19N-33W    19N-31W    19N-29W    19N-27W    19N-25W    19N-23W    19N-21W    19N-19W    19N-17W    17N-59W    17N-57W    17N-55W    17N-53W    17N-51W    17N-49W    17N-47W    17N-45W    17N-43W    17N-41W    17N-39W    17N-37W    17N-35W    17N-33W    17N-31W    17N-29W    17N-27W    17N-25W    17N-23W    17N-21W    17N-19W    17N-17W    15N-59W    15N-57W    15N-55W    15N-53W    15N-51W    15N-49W    15N-47W    15N-45W    15N-43W    15N-41W    15N-39W    15N-37W    15N-35W    15N-33W    15N-31W    15N-29W    15N-27W    15N-25W    15N-23W    15N-21W  \
1964-07-01  58.223191  65.048059  70.698303 

In [27]:
## Creating transformed df PWS full area

In [28]:
columns = pws_full_area_jul_dez_df.columns 
months = second_semester_months
pws_merged_colum_names=[]

for col in columns:
    for month in months:
        column_name = 'pws_'+ col + '_' +str(month)
        pws_merged_colum_names.append(column_name)

        #For debug only        
# for column_name in merged_colum_names:
#     print(column_name)
            

In [29]:
pws_transformed_df = pd.DataFrame(index=range(1973,2018,1), columns=pws_merged_colum_names)

for year in range(1973,2018,1):
#     print("Year " , year) #For debug only
    for month in range(7,13,1):
        for pws_column in pws_full_area_jul_dez_df.columns:
            value = pws_full_area_jul_dez_df.loc[str(year)+'-'+str(month)+'-01'][pws_column]
            column_name = 'pws_' +pws_column+'_'+str(month)
            pws_transformed_df.set_value(year, column_name, value)

In [30]:
pws_transformed_df = create_transformed_df(pws_full_area_jul_dez_df, "pws_")

In [31]:
pws_transformed_df.head()

pws_29N-59W_7 pws_29N-59W_8 pws_29N-59W_9 pws_29N-59W_10 pws_29N-59W_11 pws_29N-59W_12 pws_29N-57W_7 pws_29N-57W_8 pws_29N-57W_9 pws_29N-57W_10 pws_29N-57W_11 pws_29N-57W_12 pws_29N-55W_7 pws_29N-55W_8 pws_29N-55W_9 pws_29N-55W_10 pws_29N-55W_11 pws_29N-55W_12 pws_29N-53W_7 pws_29N-53W_8 pws_29N-53W_9 pws_29N-53W_10 pws_29N-53W_11 pws_29N-53W_12 pws_29N-51W_7 pws_29N-51W_8 pws_29N-51W_9 pws_29N-51W_10 pws_29N-51W_11 pws_29N-51W_12 pws_29N-49W_7 pws_29N-49W_8 pws_29N-49W_9 pws_29N-49W_10 pws_29N-49W_11 pws_29N-49W_12 pws_29N-47W_7 pws_29N-47W_8 pws_29N-47W_9 pws_29N-47W_10 pws_29N-47W_11 pws_29N-47W_12 pws_29N-45W_7 pws_29N-45W_8 pws_29N-45W_9 pws_29N-45W_10 pws_29N-45W_11 pws_29N-45W_12 pws_29N-43W_7 pws_29N-43W_8 pws_29N-43W_9 pws_29N-43W_10 pws_29N-43W_11 pws_29N-43W_12 pws_29N-41W_7 pws_29N-41W_8 pws_29N-41W_9 pws_29N-41W_10 pws_29N-41W_11 pws_29N-41W_12 pws_29N-39W_7 pws_29N-39W_8 pws_29N-39W_9 pws_29N-39W_10 pws_29N-39W_11 pws_29N-39W_12 pws_29N-37W_7 pws_29N-37W_8  \
1973       17.7553       10.5802        13.497        12.3146        15.1648        33.5839       19.6881        10.412       10.6005        10.2044        14.6741        30.4631       21.3825       10.5005       7.96053         8.4214        13.8224        29.3864       22.6119       9.75141       4.87545        7.20278        9.73088        28.9698       23.7192       9.88433       2.05913        6.02993        6.05392         28.324        23.817       11.5447      0.707107        5.97746         3.1305        28.2577       22.2299        12.886       3.00167        8.25409        2.71662         27.567          20.1       13.9043       5.72713        9.36216        4.03113        28.2519       15.5003       12.4064       7.64853        8.82383        2.33452        27.5274       12.3016       12.1499        9.6933        7.57166        2.05183        25.1962       12.5399       12.5172       10.6963         6.8884        4.08044        23.2155       19.9582       13.0269   
1974       6.51153       20.3039       29.5296         4.9163        15.1212        23.3105       8.86848       15.0851       31.3957        8.94427        2.38537        15.1789       9.94032       12.0071       31.4331        12.0433        5.73847        8.86397       10.6794       9.72522       32.0657        15.0655        11.1463        2.03961       11.8338       9.85089        33.509        17.7229        12.9062        6.31269       13.2563       11.7631       34.7324        20.0385        11.7085        11.8068          14.5       14.7313       30.8084        18.0269        5.93633        16.4648       16.7048       16.5605       27.0431        16.5109        7.02638        20.0801       15.8978       17.9254       23.5936        15.6461         5.6921        21.6926        15.632        20.728       22.6736        16.1112        5.86003        21.9329       17.5308       25.6082       24.4761        16.6865        6.70075        21.4674       30.9588       29.1913   
1975       18.3448       4.64866        6.0075        4.01995        20.0691        63.0079          18.6       3.14006       7.64853        11.3635        23.4214        66.9292       18.4784       2.02237       9.65401        13.8235        23.9019        66.4037       17.4347           1.7        12.659        12.5539        23.5359        60.5657       16.4125       1.43178       15.5824        9.43027        22.4018        51.5198       16.5315       2.38537       18.2332         6.0208         21.225        40.6342       15.7544       4.30116       18.4459         4.4643        20.9351        33.1074       15.4806       5.63649        18.527        4.92443        19.2938         27.926       14.4534       7.51332        19.251        4.70106        16.6481        25.9017       15.1327       11.4004       21.1341        3.92938         13.381        24.7879       17.3442       16.4222       23.9019        3.00167        9.80816        24.2508       21.4849       21.1073   
1976       5.49181       15.3062 

In [32]:
pws_transformed_df.head()

pws_29N-59W_7 pws_29N-59W_8 pws_29N-59W_9 pws_29N-59W_10 pws_29N-59W_11 pws_29N-59W_12 pws_29N-57W_7 pws_29N-57W_8 pws_29N-57W_9 pws_29N-57W_10 pws_29N-57W_11 pws_29N-57W_12 pws_29N-55W_7 pws_29N-55W_8 pws_29N-55W_9 pws_29N-55W_10 pws_29N-55W_11 pws_29N-55W_12 pws_29N-53W_7 pws_29N-53W_8 pws_29N-53W_9 pws_29N-53W_10 pws_29N-53W_11 pws_29N-53W_12 pws_29N-51W_7 pws_29N-51W_8 pws_29N-51W_9 pws_29N-51W_10 pws_29N-51W_11 pws_29N-51W_12 pws_29N-49W_7 pws_29N-49W_8 pws_29N-49W_9 pws_29N-49W_10 pws_29N-49W_11 pws_29N-49W_12 pws_29N-47W_7 pws_29N-47W_8 pws_29N-47W_9 pws_29N-47W_10 pws_29N-47W_11 pws_29N-47W_12 pws_29N-45W_7 pws_29N-45W_8 pws_29N-45W_9 pws_29N-45W_10 pws_29N-45W_11 pws_29N-45W_12 pws_29N-43W_7 pws_29N-43W_8 pws_29N-43W_9 pws_29N-43W_10 pws_29N-43W_11 pws_29N-43W_12 pws_29N-41W_7 pws_29N-41W_8 pws_29N-41W_9 pws_29N-41W_10 pws_29N-41W_11 pws_29N-41W_12 pws_29N-39W_7 pws_29N-39W_8 pws_29N-39W_9 pws_29N-39W_10 pws_29N-39W_11 pws_29N-39W_12 pws_29N-37W_7 pws_29N-37W_8  \
1973       17.7553       10.5802        13.497        12.3146        15.1648        33.5839       19.6881        10.412       10.6005        10.2044        14.6741        30.4631       21.3825       10.5005       7.96053         8.4214        13.8224        29.3864       22.6119       9.75141       4.87545        7.20278        9.73088        28.9698       23.7192       9.88433       2.05913        6.02993        6.05392         28.324        23.817       11.5447      0.707107        5.97746         3.1305        28.2577       22.2299        12.886       3.00167        8.25409        2.71662         27.567          20.1       13.9043       5.72713        9.36216        4.03113        28.2519       15.5003       12.4064       7.64853        8.82383        2.33452        27.5274       12.3016       12.1499        9.6933        7.57166        2.05183        25.1962       12.5399       12.5172       10.6963         6.8884        4.08044        23.2155       19.9582       13.0269   
1974       6.51153       20.3039       29.5296         4.9163        15.1212        23.3105       8.86848       15.0851       31.3957        8.94427        2.38537        15.1789       9.94032       12.0071       31.4331        12.0433        5.73847        8.86397       10.6794       9.72522       32.0657        15.0655        11.1463        2.03961       11.8338       9.85089        33.509        17.7229        12.9062        6.31269       13.2563       11.7631       34.7324        20.0385        11.7085        11.8068          14.5       14.7313       30.8084        18.0269        5.93633        16.4648       16.7048       16.5605       27.0431        16.5109        7.02638        20.0801       15.8978       17.9254       23.5936        15.6461         5.6921        21.6926        15.632        20.728       22.6736        16.1112        5.86003        21.9329       17.5308       25.6082       24.4761        16.6865        6.70075        21.4674       30.9588       29.1913   
1975       18.3448       4.64866        6.0075        4.01995        20.0691        63.0079          18.6       3.14006       7.64853        11.3635        23.4214        66.9292       18.4784       2.02237       9.65401        13.8235        23.9019        66.4037       17.4347           1.7        12.659        12.5539        23.5359        60.5657       16.4125       1.43178       15.5824        9.43027        22.4018        51.5198       16.5315       2.38537       18.2332         6.0208         21.225        40.6342       15.7544       4.30116       18.4459         4.4643        20.9351        33.1074       15.4806       5.63649        18.527        4.92443        19.2938         27.926       14.4534       7.51332        19.251        4.70106        16.6481        25.9017       15.1327       11.4004       21.1341        3.92938         13.381        24.7879       17.3442       16.4222       23.9019        3.00167        9.80816        24.2508       21.4849       21.1073   
1976       5.49181       15.3062 

# Merge sst_transformed_df and pws_transformed_df

In [33]:
#For debug only
# sst_transformed_df.head()

In [34]:
#For debug only
# pws_transformed_df.head()

In [35]:
df_new = pd.concat([sst_transformed_df, pws_transformed_df], axis=1)
df_new.head()

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
1973          26.3          27.7          28.2           26.5             25           22.3          26.2          27.6            28           26.4           24.9           22.2            26          27.5          27.8           26.2           24.7           22.1          25.7          27.2          27.6             26           24.5           22.1          25.6            27          27.3           25.9           24.4           22.1          25.5          26.7          27.1           25.8           24.4           22.2          25.4          26.5            27           25.7           24.4           22.3          25.3          26.3          26.9           25.7           24.4           22.3          25.2          26.2          26.8           25.7           24.4           22.2          25.1          25.8          26.7           25.6           24.2           22.3          24.7          25.4          26.5           25.4           23.8           22.4          24.3          25.2   
1974          27.1          27.4          27.4           25.9           24.7           22.8          26.8          27.4          27.4           25.9           24.7           22.9          26.5          27.2          27.2           25.9           24.6           22.9          26.1            27          27.1           25.8           24.5             23          26.1            27          26.9           25.8           24.4           22.9          26.2          26.9          26.8           25.7           24.2           22.7          26.2          26.7          26.5           25.5           24.1           22.6          25.6          26.3          25.9           25.3             24           22.5            25          25.9          25.3           25.1             24           22.5          24.5          25.5            25           24.8           24.1           22.4          24.2          25.5            25           24.7           24.1           22.2            24          25.3   
1975          26.4          27.8          28.2           26.7           25.3           22.5          26.4          27.8            28           26.7           25.2           22.5          26.3          27.8          27.9           26.7           25.1           22.5          26.3          27.7          27.6           26.6           24.9           22.4          26.4          27.6          27.3           26.3           24.8           22.3          26.4          27.4          27.1             26           24.6           22.2          26.3          27.3          26.9           25.6           24.4           22.1          25.9          27.1          26.7           25.3           24.1           21.9          25.5          26.9          26.5           25.1           23.9           21.9          25.3          26.6          26.5             25           23.6           21.8          25.1          26.4          26.4             25           23.4             22            25          26.2   
1976          27.2          27.5 

In [36]:
rainy_classified_df

1973    normal
1974    strong
1975    normal
1976      weak
1977      weak
1978      weak
1979      weak
1980      weak
1981      weak
1982      weak
1983      weak
1984    normal
1985    strong
1986    strong
1987      weak
1988    normal
1989    normal
1990      weak
1991      weak
1992      weak
1993      weak
1994    normal
1995    normal
1996    normal
1997      weak
1998      weak
1999      weak
2000    normal
2001      weak
2002      weak
2003    normal
2004      weak
2005      weak
2006      weak
2007      weak
2008    normal
2009    normal
2010      weak
2011      weak
2012      weak
2013      weak
2014      weak
2015      weak
2016      weak
2017      weak
Name: classes, dtype: object

### Droping first row


In [37]:
rainy_classified_df.drop(1973, inplace=True)

In [38]:
rainy_classified_df

1974    strong
1975    normal
1976      weak
1977      weak
1978      weak
1979      weak
1980      weak
1981      weak
1982      weak
1983      weak
1984    normal
1985    strong
1986    strong
1987      weak
1988    normal
1989    normal
1990      weak
1991      weak
1992      weak
1993      weak
1994    normal
1995    normal
1996    normal
1997      weak
1998      weak
1999      weak
2000    normal
2001      weak
2002      weak
2003    normal
2004      weak
2005      weak
2006      weak
2007      weak
2008    normal
2009    normal
2010      weak
2011      weak
2012      weak
2013      weak
2014      weak
2015      weak
2016      weak
2017      weak
Name: classes, dtype: object

# Decrease index to make easy join by index(year)

In [39]:
rainy_classified_df.index = range(1973,2017)

In [40]:
rainy_classified_df

1973    strong
1974    normal
1975      weak
1976      weak
1977      weak
1978      weak
1979      weak
1980      weak
1981      weak
1982      weak
1983    normal
1984    strong
1985    strong
1986      weak
1987    normal
1988    normal
1989      weak
1990      weak
1991      weak
1992      weak
1993    normal
1994    normal
1995    normal
1996      weak
1997      weak
1998      weak
1999    normal
2000      weak
2001      weak
2002    normal
2003      weak
2004      weak
2005      weak
2006      weak
2007    normal
2008    normal
2009      weak
2010      weak
2011      weak
2012      weak
2013      weak
2014      weak
2015      weak
2016      weak
Name: classes, dtype: object

## Merge input and output

In [41]:
dataset_df = pd.concat([df_new, rainy_classified_df], axis=1)
dataset_df.head()

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
1973          26.3          27.7          28.2           26.5             25           22.3          26.2          27.6            28           26.4           24.9           22.2            26          27.5          27.8           26.2           24.7           22.1          25.7          27.2          27.6             26           24.5           22.1          25.6            27          27.3           25.9           24.4           22.1          25.5          26.7          27.1           25.8           24.4           22.2          25.4          26.5            27           25.7           24.4           22.3          25.3          26.3          26.9           25.7           24.4           22.3          25.2          26.2          26.8           25.7           24.4           22.2          25.1          25.8          26.7           25.6           24.2           22.3          24.7          25.4          26.5           25.4           23.8           22.4          24.3          25.2   
1974          27.1          27.4          27.4           25.9           24.7           22.8          26.8          27.4          27.4           25.9           24.7           22.9          26.5          27.2          27.2           25.9           24.6           22.9          26.1            27          27.1           25.8           24.5             23          26.1            27          26.9           25.8           24.4           22.9          26.2          26.9          26.8           25.7           24.2           22.7          26.2          26.7          26.5           25.5           24.1           22.6          25.6          26.3          25.9           25.3             24           22.5            25          25.9          25.3           25.1             24           22.5          24.5          25.5            25           24.8           24.1           22.4          24.2          25.5            25           24.7           24.1           22.2            24          25.3   
1975          26.4          27.8          28.2           26.7           25.3           22.5          26.4          27.8            28           26.7           25.2           22.5          26.3          27.8          27.9           26.7           25.1           22.5          26.3          27.7          27.6           26.6           24.9           22.4          26.4          27.6          27.3           26.3           24.8           22.3          26.4          27.4          27.1             26           24.6           22.2          26.3          27.3          26.9           25.6           24.4           22.1          25.9          27.1          26.7           25.3           24.1           21.9          25.5          26.9          26.5           25.1           23.9           21.9          25.3          26.6          26.5             25           23.6           21.8          25.1          26.4          26.4             25           23.4             22            25          26.2   
1976          27.2          27.5 

In [42]:
dataset_df.tail()

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
2013            28          28.8          28.1           27.6           25.6           23.3          27.9          28.7          28.2           27.8           25.9           23.6          27.7          28.6          28.2           27.8             26           23.7          27.6          28.4          28.1           27.7           26.1           23.8          27.6          28.2            28           27.6           26.1             24          27.6          27.9          27.9           27.5           26.1           24.1          27.4          27.7          27.6           27.2           25.9             24          27.1          27.4          27.3           26.9           25.8           23.8          26.8          27.1            27           26.7           25.5           23.6          26.4          26.8          26.7           26.5           25.3           23.4          26.1          26.5          26.4           26.3           25.1           23.2          25.8          26.1   
2014           0.8           1.5           1.3            0.7            1.4              1           0.9           1.5           1.3            0.8            1.4            1.2           0.9           1.5           1.3            0.9            1.4            1.2           0.9           1.5           1.3              1            1.4            1.3           0.9           1.5           1.4            1.2            1.4            1.3           0.9           1.5           1.5            1.3            1.3            1.3           0.9           1.4           1.6            1.4            1.1            1.1             1           1.4           1.7            1.5            1.1              1             1           1.4           1.8            1.6              1            0.9             1           1.5           1.9            1.5            0.9            0.8             1           1.5           1.9            1.5            0.8            0.7           1.1           1.6   
2015           1.4           1.2           1.5            0.7            0.6            1.4           1.5           1.3           1.6            0.7            0.8            1.4           1.6           1.3           1.6            0.7            0.8            1.2           1.6           1.3           1.6            0.7            0.9            1.1           1.6           1.3           1.6            0.7              1              1           1.6           1.4           1.5            0.7              1              1           1.6           1.4           1.5            0.8              1            0.9           1.7           1.4           1.5            0.9              1            0.9           1.7           1.4           1.6            0.9            0.9            0.8           1.7           1.4           1.6            0.9            0.9            0.7           1.6           1.4           1.7            1.1            0.9            0.6           1.6           1.3   
2016           1.5           1.6 

# Split data, train and predict

## Set train data and test data

### Set train data

In [43]:
#Removing 2017 due we don't have full 2018 available
dataset_df = dataset_df.loc['1973-01-01':'2016-12-01']

#Train
train_df = dataset_df.loc['1973-01-01':'2000-12-01']

### Set test data

In [44]:
#Test
test_df = dataset_df.loc['2000-01-01':'2016-12-01']

In [45]:
test_df.head()

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
2001          27.9          28.5          28.8             28           25.3           23.9          27.4          28.3          28.5           27.9           25.3           23.2          27.2          28.2          28.4           27.8           25.2           23.1            27          28.1          28.5           27.4             25           22.9          26.9          27.9          28.3           27.3           24.9           22.9          26.7          27.7          28.2           27.1           24.8           22.8          26.3          27.5          28.1           26.8           24.6           22.3            26          27.3          27.9           26.6           24.5           22.2            26          27.3          27.9           26.1           24.4           22.2          25.7            27          27.7             26           24.3           22.1          25.4          26.8          27.5           25.8           24.2             22          25.1          26.5   
2002          27.4          27.8            28           26.5           25.2           23.7          27.3          27.8          27.8           26.6           25.3           23.8          27.1          27.7          27.7           26.5           25.2           23.8            27          27.5          27.5           26.5           25.1           23.8          26.9          27.3          27.3           26.5           25.1           23.7          26.7          27.1          27.3           26.5             25           23.6          26.4          27.1          27.3           26.5           24.8           23.4          26.1          26.9          27.2           26.4           24.6           23.1          25.7          26.8          27.2           26.4           24.4           22.9          25.2          26.5          27.1           26.3           24.2           22.8          24.8          26.3            27           26.1             24           22.6          24.5            26   
2003          28.4          28.6          27.7           27.5           25.6           23.5          28.3          28.6          27.9           27.4           25.6           23.7          28.1          28.5            28           27.3           25.5           23.7          27.9          28.5            28             27           25.4           23.6          27.8          28.4            28           26.8           25.2           23.5          27.8          28.3          28.1           26.6             25           23.3          27.6          28.3            28           26.4           24.8           23.2          27.3          28.1          27.9           26.2           24.6             23          27.1            28          27.7           26.2           24.2           22.8          26.9          27.7          27.5           26.2           23.9           22.7          26.6          27.4          27.4           26.2           23.5           22.6          26.4          27.1   
2004            28          28.7 

In [46]:
train_df.tail()

sst_29N-59W_7 sst_29N-59W_8 sst_29N-59W_9 sst_29N-59W_10 sst_29N-59W_11 sst_29N-59W_12 sst_29N-57W_7 sst_29N-57W_8 sst_29N-57W_9 sst_29N-57W_10 sst_29N-57W_11 sst_29N-57W_12 sst_29N-55W_7 sst_29N-55W_8 sst_29N-55W_9 sst_29N-55W_10 sst_29N-55W_11 sst_29N-55W_12 sst_29N-53W_7 sst_29N-53W_8 sst_29N-53W_9 sst_29N-53W_10 sst_29N-53W_11 sst_29N-53W_12 sst_29N-51W_7 sst_29N-51W_8 sst_29N-51W_9 sst_29N-51W_10 sst_29N-51W_11 sst_29N-51W_12 sst_29N-49W_7 sst_29N-49W_8 sst_29N-49W_9 sst_29N-49W_10 sst_29N-49W_11 sst_29N-49W_12 sst_29N-47W_7 sst_29N-47W_8 sst_29N-47W_9 sst_29N-47W_10 sst_29N-47W_11 sst_29N-47W_12 sst_29N-45W_7 sst_29N-45W_8 sst_29N-45W_9 sst_29N-45W_10 sst_29N-45W_11 sst_29N-45W_12 sst_29N-43W_7 sst_29N-43W_8 sst_29N-43W_9 sst_29N-43W_10 sst_29N-43W_11 sst_29N-43W_12 sst_29N-41W_7 sst_29N-41W_8 sst_29N-41W_9 sst_29N-41W_10 sst_29N-41W_11 sst_29N-41W_12 sst_29N-39W_7 sst_29N-39W_8 sst_29N-39W_9 sst_29N-39W_10 sst_29N-39W_11 sst_29N-39W_12 sst_29N-37W_7 sst_29N-37W_8  \
1996          27.5          27.9            28           26.8           24.9           22.3            27            28          28.2           26.8           24.9           22.5          26.8          27.8          28.1           26.7           24.9           22.5          26.7          27.6          27.9           26.6           24.7           22.6          26.5          27.4          27.7           26.5           24.6           22.5          26.4          27.2          27.6           26.3           24.5           22.5          25.8          26.8          27.6           26.3           24.6           22.4          25.5          26.6          27.4           26.1           24.5           22.3          25.2          26.1          27.2             26           24.4           22.3          24.9          25.8            27           25.9           24.3           22.2          24.6          25.6          26.8           25.7           24.2           22.1          23.9          25.2   
1997          28.1          29.1          27.8           26.3           24.1           22.6          27.8          28.9          28.2           26.4           24.1           22.7          27.6          28.8          28.1           26.3             24           22.7          27.4          28.3          28.2           26.4           24.2           22.8          27.3          28.1            28           26.2           24.1           22.8          27.2          27.9          27.9           26.1             24           22.7          26.8          27.5          28.1           26.2           24.2           22.9          26.5          27.3          27.9           26.1           24.1           22.8          26.5          27.1          27.9             26             24           22.7          26.2          26.8          27.7           25.9           23.9           22.6          25.9          26.6          27.5           25.7           23.8           22.5          25.4          26.5   
1998          27.6          28.1          28.9           27.3           25.6           23.9          27.3            28          28.6             27           25.5           23.6          27.1          27.9          28.5           26.9           25.4           23.6          26.8          27.7          28.3           26.8           25.4           23.7          26.7          27.5          28.1           26.7           25.3           23.7          26.5          27.3            28           26.6           25.2           23.6          26.3          27.3          27.8           26.4           25.3           23.2            26          27.1          27.6           26.2           25.2           23.1          25.9          27.1          27.2           26.3           25.3           23.2          25.6          26.8            27           26.2           25.2           23.1          25.3          26.6          26.8             26             25             23          25.1          26.4   
1999          28.2          29.1 

### Keep last column(classes) as target

In [47]:
feature_cols = dataset_df.columns
feature_cols=feature_cols.drop('classes')

In [48]:
feature_cols

Index(['sst_29N-59W_7', 'sst_29N-59W_8', 'sst_29N-59W_9', 'sst_29N-59W_10', 'sst_29N-59W_11', 'sst_29N-59W_12', 'sst_29N-57W_7', 'sst_29N-57W_8', 'sst_29N-57W_9', 'sst_29N-57W_10',
       ...
       'pws_19S-11E_9', 'pws_19S-11E_10', 'pws_19S-11E_11', 'pws_19S-11E_12', 'pws_19S-13E_7', 'pws_19S-13E_8', 'pws_19S-13E_9', 'pws_19S-13E_10', 'pws_19S-13E_11', 'pws_19S-13E_12'], dtype='object', length=7536)

### Input data (X)

In [49]:
X = train_df.loc[:, feature_cols]

### Output data (y)

In [50]:
y = train_df['classes']

### Testing

In [51]:
X_test = test_df.loc[:, feature_cols]


In [52]:
X_test.shape


(16, 7536)

# Applyng classifiers

## Testing KNN (with k=3)

In [53]:
def test_knn(X,y):
    
    knn = KNeighborsClassifier(n_neighbors=3)

    knn.fit(X, y)
    new_pred_class = knn.predict(X_test)
    metrics.accuracy_score(test_df['classes'], new_pred_class)
    year = 2001
    for v in new_pred_class:
        print(year, v)
    return new_pred_class

In [54]:
new_pred_class = test_knn(X,y)

2001 normal
2001 weak
2001 weak
2001 weak
2001 weak
2001 normal
2001 normal
2001 weak
2001 normal
2001 normal
2001 normal
2001 weak
2001 weak
2001 normal
2001 weak
2001 weak


In [55]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5

In [56]:
def test_svc(X,y):
    svc = SVC()
    svc.fit(X, y)
    new_pred_class = svc.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [57]:
new_pred_class = test_svc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [58]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

### GaussianProcessClassifier

In [59]:
def test_gpc(X,y):
    gpc = GaussianProcessClassifier()
    gpc.fit(X, y)
    new_pred_class = gpc.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [60]:
new_pred_class = test_gpc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [61]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

### Decision Tree

In [62]:
def test_dtc(X,y):

    dtc = DecisionTreeClassifier(random_state=1)
    dtc.fit(X, y)
    new_pred_class = dtc.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [63]:
new_pred_class = test_dtc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 normal
2014 normal
2015 normal
2016 normal


In [64]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5625

### RandomForestClassifier

In [65]:
def test_rfc(X,y):

    rfc = RandomForestClassifier(random_state=1)
    rfc.fit(X, y)
    new_pred_class = rfc.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [66]:
new_pred_class = test_rfc(X,y)

2001 normal
2002 normal
2003 normal
2004 normal
2005 weak
2006 normal
2007 normal
2008 normal
2009 normal
2010 normal
2011 weak
2012 normal
2013 normal
2014 weak
2015 weak
2016 weak


In [67]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5

### MLPClassifier

In [68]:
def test_mlp(X,y):
    mlp = MLPClassifier(random_state=1)
    mlp.fit(X, y)
    new_pred_class = mlp.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [69]:
new_pred_class = test_mlp(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [70]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [71]:
### sklearn.ensemble.AdaBoostClassifier

In [72]:
def test_adc(X,y):
    adc = AdaBoostClassifier(random_state=1)
    adc.fit(X, y)
    new_pred_class = adc.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [73]:
new_pred_class = test_adc(X,y)

2001 weak
2002 normal
2003 weak
2004 weak
2005 weak
2006 normal
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [74]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

### GaussianNB

In [75]:
def test_gnb(X,y):
    gnb = GaussianNB()
    gnb.fit(X, y)
    new_pred_class = gnb.predict(X_test)
    year = 2001
    for v in new_pred_class:
        print(year, v)
        year += 1
    return new_pred_class

In [76]:
new_pred_class = test_gnb(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [77]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

### Init columns form regions: ATN, ATS, TN, TS

In [78]:
colunas_atn_n = constroi_colunas_latitude_longitude(init_lat=19, end_lat=0,
                                                    init_long=49, end_long=20)

colunas_atn_s = constroi_colunas_latitude_longitude(init_lat=-1, end_lat=-17,
                                                    init_long=29, end_long=0)

colunas_tn = constroi_colunas_latitude_longitude(init_lat=27, end_lat=3,
                                                    init_long=59, end_long=17)

colunas_ts = constroi_colunas_latitude_longitude(init_lat=5, end_lat=-20,
                                                    init_long=59, end_long=-17)

### Init dataframes from : ATN, ATS, TN, TS

In [79]:
atn_sst_df=pd.DataFrame(sst_full_area_jul_dez_df, index=sst_full_area_jul_dez_df.index, columns=colunas_atn_n)
ats_sst_df=pd.DataFrame(sst_full_area_jul_dez_df, index=sst_full_area_jul_dez_df.index, columns=colunas_atn_s)
tn_sst_df=pd.DataFrame(sst_full_area_jul_dez_df, index=sst_full_area_jul_dez_df.index, columns=colunas_tn)
ts_sst_df=pd.DataFrame(sst_full_area_jul_dez_df, index=sst_full_area_jul_dez_df.index, columns=colunas_ts)

atn_pws_df=pd.DataFrame(pws_full_area_jul_dez_df, index=pws_full_area_jul_dez_df.index, columns=colunas_atn_n)
ats_pws_df=pd.DataFrame(pws_full_area_jul_dez_df, index=pws_full_area_jul_dez_df.index, columns=colunas_atn_s)
tn_pws_df=pd.DataFrame(pws_full_area_jul_dez_df, index=pws_full_area_jul_dez_df.index, columns=colunas_tn)
ts_pws_df=pd.DataFrame(pws_full_area_jul_dez_df, index=pws_full_area_jul_dez_df.index, columns=colunas_ts)

In [80]:
atn_sst_df.head()

19N-49W  19N-47W  19N-45W  19N-43W  19N-41W  19N-39W  19N-37W  19N-35W  19N-33W  19N-31W  19N-29W  19N-27W  19N-25W  19N-23W  19N-21W  17N-49W  17N-47W  17N-45W  17N-43W  17N-41W  17N-39W  17N-37W  17N-35W  17N-33W  17N-31W  17N-29W  17N-27W  17N-25W  17N-23W  17N-21W  15N-49W  15N-47W  15N-45W  15N-43W  15N-41W  15N-39W  15N-37W  15N-35W  15N-33W  15N-31W  15N-29W  15N-27W  15N-25W  15N-23W  15N-21W  13N-49W  13N-47W  13N-45W  13N-43W  13N-41W  13N-39W  13N-37W  13N-35W  13N-33W  13N-31W  13N-29W  13N-27W  13N-25W  13N-23W  13N-21W  11N-49W  11N-47W  11N-45W  11N-43W  11N-41W  11N-39W  11N-37W  11N-35W  11N-33W  11N-31W  11N-29W  11N-27W  11N-25W  11N-23W  11N-21W  9N-49W  9N-47W  9N-45W  9N-43W  9N-41W  9N-39W  9N-37W  9N-35W  9N-33W  9N-31W  9N-29W  9N-27W  9N-25W  9N-23W  9N-21W  7N-49W  7N-47W  7N-45W  7N-43W  7N-41W  7N-39W  7N-37W  7N-35W  7N-33W  7N-31W  7N-29W  7N-27W  7N-25W  7N-23W  7N-21W  5N-49W  5N-47W  5N-45W  5N-43W  5N-41W  5N-39W  5N-37W  5N-35W  5N-33W  \
1973-07-01     26.5     26.0     25.8     25.6     25.3     25.1     24.8     24.5     24.3     24.1     24.1     23.9     23.5     23.2     23.1     26.5     25.9     25.8     25.6     25.5     25.4     25.3     25.1     24.9     24.7     24.6     24.4     24.2     24.0     24.7     26.4     26.1     25.8     25.8     25.8     25.7     25.6     25.6     25.6     25.5     25.6     25.5     25.3     25.3     26.0     26.6     26.5     26.4     26.4     26.1     25.9     25.9     26.1     26.3     26.5     26.6     26.6     26.4     26.5     27.0     27.1     27.2     27.2     27.2     26.8     26.6     26.5     26.6     26.9     27.2     27.3     27.3     27.3     27.4     27.8    27.6    27.7    27.8    27.9    27.7    27.5    27.4    27.4    27.5    27.6    27.6    27.6    27.8    28.0    28.1    27.8    27.9    28.0    28.2    28.3    28.3    28.2    28.0    28.0    27.8    27.7    27.7    28.0    28.2    28.3    27.7    27.8    28.0    28.2    28.4    28.5    28.6    28.2    27.9   
1973-08-01     27.0     26.8     26.4     26.0     25.7     25.4     25.2     25.1     25.0     24.9     24.7     24.5     24.5     24.5     24.5     27.1     26.8     26.6     26.2     26.0     25.8     25.7     25.7     25.7     25.7     25.7     25.5     25.3     25.3     25.9     27.0     26.9     26.6     26.5     26.4     26.4     26.3     26.3     26.3     26.4     26.4     26.4     26.3     26.3     26.8     27.1     27.0     27.0     27.0     27.0     27.1     27.0     27.0     26.9     26.9     27.0     27.1     26.9     27.0     27.3     27.6     27.7     27.7     27.7     27.8     27.8     27.7     27.6     27.5     27.4     27.4     27.3     27.3     27.4     27.4    28.2    28.3    28.4    28.5    28.5    28.4    28.2    28.1    28.0    27.8    27.6    27.4    27.4    27.5    27.5    28.4    28.4    28.6    28.8    28.9    28.7    28.5    28.4    28.4    28.1    27.7    27.4    27.6    27.6    27.4    28.1    28.1    28.3    28.6    28.7    28.6    28.5    28.5    28.3   
1973-09-01     27.1     26.9     26.8     26.7     26.7     26.6     26.4     26.0     25.6     25.2     25.1     25.1     25.3     25.4     25.3     27.2     27.0     26.9     26.8     26.8     26.7     26.6     26.5     26.4     26.2     26.0     25.9     25.9     26.2     26.7     27.4     27.3     27.0     26.9     26.9     26.8     26.8     26.9     27.0     27.1     26.9     26.7     26.6     26.9     27.4     27.9     27.7     27.4     27.1     27.0     26.9     26.9     27.1     27.3     27.5     27.4     27.2     27.1     27.3     27.6     28.5     28.4     28.0     27.6     27.3     27.3     27.2     27.3     27.5     27.6     27.5     27.4     27.3     27.4     27.5    28.9    28.8    28.6    28.4    28.1    28.0    27.9    27.9    27.9    27.8    27.7    27.5    27.5    27.5    27.4    28.7    28.9    28.9    28.8    28.7    28.6    28.6    28.4    28.2    28.0    27.7    27.7    27.7    27.6    27.4    28.3    28.6    28.8    28.8    28.8    28.9    28.8    28.5    28.1   
1973-10-

In [81]:
ats_sst_df.head()

1S-29W  1S-27W  1S-25W  1S-23W  1S-21W  1S-19W  1S-17W  1S-15W  1S-13W  1S-11W  1S-9W  1S-7W  1S-5W  1S-3W  1S-1W  3S-29W  3S-27W  3S-25W  3S-23W  3S-21W  3S-19W  3S-17W  3S-15W  3S-13W  3S-11W  3S-9W  3S-7W  3S-5W  3S-3W  3S-1W  5S-29W  5S-27W  5S-25W  5S-23W  5S-21W  5S-19W  5S-17W  5S-15W  5S-13W  5S-11W  5S-9W  5S-7W  5S-5W  5S-3W  5S-1W  7S-29W  7S-27W  7S-25W  7S-23W  7S-21W  7S-19W  7S-17W  7S-15W  7S-13W  7S-11W  7S-9W  7S-7W  7S-5W  7S-3W  7S-1W  9S-29W  9S-27W  9S-25W  9S-23W  9S-21W  9S-19W  9S-17W  9S-15W  9S-13W  9S-11W  9S-9W  9S-7W  9S-5W  9S-3W  9S-1W  11S-29W  11S-27W  11S-25W  11S-23W  11S-21W  11S-19W  11S-17W  11S-15W  11S-13W  11S-11W  11S-9W  11S-7W  11S-5W  11S-3W  11S-1W  13S-29W  13S-27W  13S-25W  13S-23W  13S-21W  13S-19W  13S-17W  13S-15W  13S-13W  13S-11W  13S-9W  13S-7W  13S-5W  13S-3W  13S-1W  15S-29W  15S-27W  15S-25W  15S-23W  15S-21W  15S-19W  15S-17W  15S-15W  15S-13W  15S-11W  15S-9W  15S-7W  15S-5W  15S-3W  15S-1W  17S-29W  17S-27W  \
1973-07-01    26.8    27.3    26.7    25.9    25.5    25.4    25.2    24.6    23.9    23.1   23.2   23.5   24.3   25.1   25.2    27.1    27.3    26.7    26.0    25.4    25.2    25.1    24.7    24.0    23.5   23.4   23.4   23.7   24.1   24.2    27.2    26.9    26.4    26.0    25.7    25.4    25.0    24.8    24.7    24.4   24.0   23.8   23.8   23.8   23.9    27.0    26.5    26.1    25.8    25.7    25.4    25.1    25.0    25.5    25.4   24.5   24.1   24.0   23.9   23.7    26.6    26.0    25.7    25.4    25.1    24.9    24.8    25.3    25.7    25.7   24.9   24.1   24.0   23.8   23.6     26.2     25.7     25.3     24.9     24.6     24.4     24.5     25.0     25.4     25.2    24.4    23.6    23.4    23.4    23.2     25.8     25.5     25.1     24.7     24.5     24.3     24.2     24.3     24.3     24.0    23.4    22.8    22.7    22.7    22.4     25.6     25.3     25.1     24.7     24.5     24.3     24.0     23.4     23.0     22.6    22.4    22.2    22.1    22.1    21.7     25.6     25.4   
1973-08-01    27.0    27.0    26.4    25.6    25.3    25.2    25.2    24.6    24.1    23.8   23.8   23.8   23.9   24.0   24.1    27.0    27.0    26.4    25.6    25.1    25.1    24.9    24.6    24.2    23.8   23.6   23.5   23.3   23.2   23.0    27.0    26.7    26.3    25.7    25.2    24.9    24.7    24.7    24.6    24.4   24.0   23.6   23.4   23.2   22.9    26.8    26.5    26.2    26.0    25.5    25.0    24.7    24.7    24.6    24.5   24.2   23.7   23.5   23.2   23.1    26.5    26.2    26.1    25.9    25.6    25.2    24.7    24.5    24.3    24.0   23.7   23.5   23.2   22.9   22.7     26.1     25.7     25.6     25.5     25.3     25.2     24.9     24.1     23.4     23.1    23.0    22.9    22.6    22.3    22.0     25.8     25.2     24.9     24.7     24.9     24.9     24.7     23.9     22.8     22.3    22.2    22.1    21.9    21.5    21.2     25.6     24.9     24.4     24.2     24.3     24.5     24.3     23.5     22.5     21.9    21.6    21.5    21.1    20.8    20.6     25.2     24.7   
1973-09-01    26.8    26.9    26.3    25.6    25.3    25.3    25.2    24.9    24.6    24.4   24.3   24.4   24.4   24.6   25.0    27.1    27.2    26.3    25.4    25.2    25.2    25.1    24.6    24.1    23.9   23.9   23.9   23.8   23.8   24.0    27.1    27.1    26.5    25.8    25.5    25.5    25.3    24.7    24.2    23.9   23.8   23.7   23.6   23.6   23.6    26.8    26.9    26.5    26.0    25.7    25.8    25.6    25.0    24.3    24.0   23.6   23.3   23.2   23.2   23.1    26.7    26.6    26.3    26.0    25.7    25.7    25.6    25.0    24.3    23.8   23.3   23.2   22.8   22.6   22.5     26.2     26.3     25.9     25.5     25.4     25.6     25.4     24.8     24.1     23.5    23.2    22.8    22.4    22.0    21.9     25.7     25.9     25.4     24.8     24.8     25.0     25.1     24.4     23.6     23.1    22.9    22.6    22.0    21.5    21.1     25.4     25.5     24.9     24.4     24.2     24.2     24.2     23.7     23.0     22.6    22.4    22.1    21.6    21.1    20.5     25.2     25.0   
1973-10-01    27.1    27

In [82]:
tn_sst_df.head()

27N-59W  27N-57W  27N-55W  27N-53W  27N-51W  27N-49W  27N-47W  27N-45W  27N-43W  27N-41W  27N-39W  27N-37W  27N-35W  27N-33W  27N-31W  27N-29W  27N-27W  27N-25W  27N-23W  27N-21W  27N-19W  27N-17W  25N-59W  25N-57W  25N-55W  25N-53W  25N-51W  25N-49W  25N-47W  25N-45W  25N-43W  25N-41W  25N-39W  25N-37W  25N-35W  25N-33W  25N-31W  25N-29W  25N-27W  25N-25W  25N-23W  25N-21W  25N-19W  25N-17W  23N-59W  23N-57W  23N-55W  23N-53W  23N-51W  23N-49W  23N-47W  23N-45W  23N-43W  23N-41W  23N-39W  23N-37W  23N-35W  23N-33W  23N-31W  23N-29W  23N-27W  23N-25W  23N-23W  23N-21W  23N-19W  23N-17W  21N-59W  21N-57W  21N-55W  21N-53W  21N-51W  21N-49W  21N-47W  21N-45W  21N-43W  21N-41W  21N-39W  21N-37W  21N-35W  21N-33W  21N-31W  21N-29W  21N-27W  21N-25W  21N-23W  21N-21W  21N-19W  21N-17W  19N-59W  19N-57W  19N-55W  19N-53W  19N-51W  19N-49W  19N-47W  19N-45W  19N-43W  19N-41W  19N-39W  19N-37W  19N-35W  19N-33W  19N-31W  19N-29W  19N-27W  19N-25W  19N-23W  19N-21W  19N-19W  \
1973-07-01     26.9     26.7     26.4     26.1     25.9     25.7     25.5     25.4     25.2     24.9     24.6     24.2     23.9     23.6     23.4     23.2     23.0     22.7     22.3     22.0     21.6     21.0     27.4     27.2     26.8     26.5     26.2     26.0     25.8     25.5     25.1     24.7     24.4     24.1     23.8     23.5     23.4     23.4     23.4     23.0     22.4     21.9     21.1     20.3     27.6     27.4     27.2     26.8     26.5     26.3     26.1     25.6     25.2     24.7     24.5     24.1     23.8     23.6     23.6     23.7     23.6     23.2     22.6     21.7     20.6     19.5     27.8     27.6     27.3     27.0     26.8     26.5     26.1     25.7     25.3     25.0     24.7     24.4     24.1     23.9     23.9     23.8     23.7     23.4     22.9     22.0     21.2     20.5     27.9     27.7     27.5     27.3     26.9     26.5     26.0     25.8     25.6     25.3     25.1     24.8     24.5     24.3     24.1     24.1     23.9     23.5     23.2     23.1     23.3   
1973-08-01     27.8     27.7     27.4     27.1     26.9     26.6     26.3     26.1     25.9     25.5     25.2     24.9     24.6     24.2     24.0     23.8     23.5     23.3     23.1     22.6     22.0     21.3     27.7     27.6     27.4     27.1     26.8     26.5     26.3     26.0     25.6     25.3     25.0     24.8     24.3     23.8     23.5     23.4     23.3     23.3     23.0     22.5     21.4     20.4     27.7     27.6     27.4     27.2     26.9     26.7     26.4     26.0     25.5     25.3     25.1     24.8     24.3     23.8     23.4     23.3     23.2     23.4     23.3     22.5     21.2     19.8     27.7     27.6     27.5     27.3     27.1     26.9     26.5     26.2     25.8     25.4     25.2     24.9     24.6     24.4     24.0     23.7     23.6     23.7     23.7     23.2     22.3     21.3     27.8     27.7     27.5     27.3     27.2     27.0     26.8     26.4     26.0     25.7     25.4     25.2     25.1     25.0     24.9     24.7     24.5     24.5     24.5     24.5     24.5   
1973-09-01     28.3     28.1     27.8     27.5     27.2     27.1     26.9     26.7     26.6     26.4     26.1     25.8     25.6     25.3     25.1     25.0     24.7     24.3     23.7     23.1     22.6     22.0     28.2     28.0     27.7     27.4     27.1     26.9     26.8     26.6     26.3     26.0     25.8     25.5     25.3     24.9     24.8     24.9     24.7     24.4     23.9     23.1     22.0     20.9     28.0     27.8     27.6     27.3     27.0     26.9     26.8     26.5     26.2     26.0     25.8     25.5     25.1     24.8     24.7     24.6     24.6     24.6     24.1     23.1     21.6     20.0     27.8     27.7     27.5     27.3     27.1     27.0     26.8     26.7     26.5     26.4     26.2     25.9     25.5     25.0     24.6     24.6     24.7     24.8     24.7     23.8     22.5     21.0     27.8     27.7     27.6     27.4     27.2     27.1     26.9     26.8     26.7     26.7     26.6     26.4     26.0     25.6     25.2     25.1     25.1     25.3     25.4     25.3     24.9   
1973-10-01     27.0     26.9    

In [83]:
ts_sst_df.head()

5N-59W  5N-57W  5N-55W  5N-53W  5N-51W  5N-49W  5N-47W  5N-45W  5N-43W  5N-41W  5N-39W  5N-37W  5N-35W  5N-33W  5N-31W  5N-29W  5N-27W  5N-25W  5N-23W  5N-21W  5N-19W  5N-17W  5N-15W  5N-13W  5N-11W  5N-9W  5N-7W  5N-5W  5N-3W  5N-1W  5N-1E  5N-3E  5N-5E  5N-7E  5N-9E  5N-11E  5N-13E  5N-15E  3N-59W  3N-57W  3N-55W  3N-53W  3N-51W  3N-49W  3N-47W  3N-45W  3N-43W  3N-41W  3N-39W  3N-37W  3N-35W  3N-33W  3N-31W  3N-29W  3N-27W  3N-25W  3N-23W  3N-21W  3N-19W  3N-17W  3N-15W  3N-13W  3N-11W  3N-9W  3N-7W  3N-5W  3N-3W  3N-1W  3N-1E  3N-3E  3N-5E  3N-7E  3N-9E  3N-11E  3N-13E  3N-15E  1N-59W  1N-57W  1N-55W  1N-53W  1N-51W  1N-49W  1N-47W  1N-45W  1N-43W  1N-41W  1N-39W  1N-37W  1N-35W  1N-33W  1N-31W  1N-29W  1N-27W  1N-25W  1N-23W  1N-21W  1N-19W  1N-17W  1N-15W  1N-13W  1N-11W  1N-9W  1N-7W  1N-5W  1N-3W  1N-1W  1N-1E  1N-3E  1N-5E  1N-7E  1N-9E  1N-11E  1N-13E  1N-15E  1S-59W  1S-57W  1S-55W  1S-53W  1S-51W  1S-49W  1S-47W  1S-45W  1S-43W  1S-41W  1S-39W  1S-37W  1S-35W  \
1973-07-01     NaN     NaN     NaN     NaN    27.8    27.7    27.8    28.0    28.2    28.4    28.5    28.6    28.2    27.9    27.8    27.7    27.8    27.9    28.0    27.8    27.4    27.2    27.3    27.3    27.4   27.5   27.4   27.0   26.8   26.7   27.2   27.8   28.1   28.2   28.4     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    27.8    27.8    27.9    28.1    28.3    28.4    28.3    27.9    27.5    27.3    27.3    27.5    27.4    27.1    26.9    26.7    26.7    26.4    26.1    26.1   26.3   26.6   26.9   27.1   27.3   27.3   27.4   27.5   27.4   27.3     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    28.0    28.0    27.9    27.9    28.0    28.1    28.0    27.5    26.9    26.6    26.9    27.2    26.8    26.2    26.0    25.9    25.8    25.3    24.6    24.2   24.4   24.9   25.7   26.4   26.6   26.5   26.0   25.8   25.6   25.4     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    28.2    27.9    27.8    27.8    27.9    27.8    27.2   
1973-08-01     NaN     NaN     NaN     NaN    28.5    28.1    28.1    28.3    28.6    28.7    28.6    28.5    28.5    28.3    28.0    27.7    27.4    27.4    27.3    26.9    26.5    26.3    26.6    26.9    26.9   26.4   25.6   25.1   24.9   24.9   25.5   26.3   27.0   27.6   27.8     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    27.7    27.4    27.7    28.2    28.4    28.3    28.2    28.1    28.0    27.6    27.3    27.2    27.0    26.6    26.1    25.8    25.7    25.9    26.1    26.2   26.0   25.7   25.6   25.5   25.6   25.9   26.4   26.8   27.2   27.4     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    27.5    27.1    27.4    27.9    28.1    28.0    27.8    27.6    27.4    27.1    27.1    27.1    26.5    26.0    25.6    25.4    25.3    25.1    24.9    24.9   24.8   24.9   25.1   25.2   25.4   25.5   25.8   26.1   26.3   26.4     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    27.0    27.5    27.8    27.8    27.7    27.6    27.3   
1973-09-01     NaN     NaN     NaN     NaN    28.1    28.3    28.6    28.8    28.8    28.8    28.9    28.8    28.5    28.1    27.7    27.6    27.6    27.6    27.5    27.3    27.1    27.0    27.1    27.1    27.1   26.8   26.1   25.5   25.3   25.3   25.6   26.1   26.5   26.9   27.1     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    28.2    28.4    28.4    28.4    28.5    28.7    28.8    28.3    27.5    27.1    27.1    27.3    27.2    27.0    26.7    26.5    26.6    26.7    26.7    26.6   26.4   26.1   25.9   25.9   26.0   26.3   26.6   26.8   26.8   26.9     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    28.5    28.4    28.1    27.9    28.0    28.3    28.4    27.9    27.2    26.6    26.8    27.0    26.6    26.2    26.0    25.8    25.8    25.8    25.8    25.6   25.4   25.3   25.5   25.6   26.0   26.4   26.8   26.7   26.6   26.4     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    28.4    27.7    27.3    27.4    27.7    27.7    27.3   
1973-10-01  

In [84]:
atn_pws_df.head()

19N-49W    19N-47W    19N-45W    19N-43W    19N-41W    19N-39W    19N-37W    19N-35W    19N-33W    19N-31W    19N-29W    19N-27W    19N-25W    19N-23W    19N-21W    17N-49W    17N-47W    17N-45W    17N-43W    17N-41W    17N-39W    17N-37W    17N-35W    17N-33W    17N-31W    17N-29W    17N-27W    17N-25W    17N-23W    17N-21W    15N-49W    15N-47W    15N-45W    15N-43W    15N-41W    15N-39W    15N-37W    15N-35W    15N-33W    15N-31W    15N-29W    15N-27W    15N-25W    15N-23W    15N-21W    13N-49W    13N-47W    13N-45W    13N-43W    13N-41W    13N-39W    13N-37W    13N-35W    13N-33W    13N-31W    13N-29W    13N-27W    13N-25W    13N-23W    13N-21W    11N-49W    11N-47W    11N-45W    11N-43W    11N-41W    11N-39W    11N-37W    11N-35W    11N-33W    11N-31W    11N-29W    11N-27W    11N-25W    11N-23W    11N-21W     9N-49W     9N-47W     9N-45W     9N-43W     9N-41W     9N-39W     9N-37W     9N-35W     9N-33W     9N-31W     9N-29W     9N-27W     9N-25W     9N-23W  \
1964-07-01  67.856098  72.996507  75.961372  74.215901  70.785945  68.379017  64.066372  60.421519  58.495812  56.738787  52.031721  48.100104  43.744371  38.006315  33.670313  76.068456  81.049676  81.334863  75.156171  68.557859  64.349747  59.255464  53.480931  48.766895  45.009888  40.451576  38.612174  35.361702  28.589683  22.496444  79.030247  82.697340  79.477607  70.677083  64.464331  61.417668  56.690387  50.835126  42.479289  33.835484  27.650136  25.785655  23.982702  19.682480  13.717872  70.208974  71.627160  65.774235  58.052735  53.251479  53.180636  51.807818  47.164499  36.889294  25.179357  16.119864  12.442267  10.938464   9.812747   8.080223  49.556533  48.287990  41.893675  36.654740  35.202983  38.608030  40.838340  37.822877  28.400704  15.920113   4.604346   2.570992   6.600758   8.302409  10.435516  26.752383  24.464055  18.317478  13.780058  15.860013  20.620621  24.573360  23.669812  16.763055   9.620811   8.237718  11.458621  14.873466  16.901183   
1964-08-01  60.848172  62.391025  60.756070  56.928815  54.610713  55.989285  63.029200  66.813921  67.285957  63.770605  56.660127  46.003696  37.835565  34.934367  35.179113  62.400080  63.779777  62.140566  58.263539  56.766539  59.387709  64.843350  67.635789  64.646191  57.502174  47.852377  38.897301  32.086134  26.892378  23.963514  53.048657  54.803011  52.646842  49.370538  49.289350  52.546360  55.193931  56.240288  50.280016  39.636978  29.093126  22.973028  17.960234  13.376472  10.829589  37.697745  38.124270  34.842072  30.758576  29.076623  32.316714  34.845947  34.112314  27.264079  17.608237   8.184131   3.157531   5.656854   8.471718  10.938464  22.240728  21.092416  15.311434   8.246211   5.780138   6.489992   8.964374   9.231468   4.909175   1.868154   9.501579  17.748521  23.915267  26.728636  27.882970  13.031117  10.186756   6.365532   8.286133  13.325539  16.070159  13.645878  11.232987  11.567627  14.491722  20.888753  31.405891  39.624361  43.176498   
1964-09-01  47.306871  48.926475  47.856556  43.500000  37.675058  34.189180  36.682421  41.797249  48.606584  53.462697  53.475976  49.814255  44.740362  39.817710  34.761041  49.526155  50.743670  49.156485  44.678630  39.014997  33.572161  34.124771  37.308578  42.764939  45.551729  44.936066  41.900477  37.901187  32.054485  24.936920  46.416484  46.253432  43.811528  39.069809  33.209938  27.821035  25.799225  27.455418  30.761177  32.756679  31.876324  30.423675  28.560812  23.113849  16.507574  37.555825  35.706162  32.719566  28.139119  22.316362  17.601136  15.061540  15.098675  16.462381  17.715812  17.439323  17.886867  17.007351  14.142136  10.288343  26.672083  23.516165  20.496341  16.601807  12.041595   9.272001   7.516648   4.751842   3.733631   3.492850   4.729693   6.628725   7.655064   8.174350   8.729834  20.072120  17.383325  15.849290  11.905041   5.600893   1.720465   3.436568   5.745433   8.561542  10.705606  10.454664  11.920151  14.949582  17.750493   
1964-10-01  29.400170  34.800575  36.80000

In [85]:
ats_pws_df.head()

1S-29W     1S-27W     1S-25W     1S-23W     1S-21W     1S-19W     1S-17W     1S-15W     1S-13W     1S-11W      1S-9W      1S-7W      1S-5W      1S-3W      1S-1W     3S-29W     3S-27W     3S-25W     3S-23W     3S-21W     3S-19W     3S-17W     3S-15W     3S-13W     3S-11W      3S-9W      3S-7W      3S-5W      3S-3W      3S-1W     5S-29W     5S-27W     5S-25W     5S-23W     5S-21W     5S-19W     5S-17W     5S-15W     5S-13W     5S-11W      5S-9W      5S-7W      5S-5W      5S-3W      5S-1W     7S-29W     7S-27W     7S-25W     7S-23W     7S-21W     7S-19W     7S-17W     7S-15W     7S-13W     7S-11W      7S-9W      7S-7W      7S-5W      7S-3W      7S-1W     9S-29W     9S-27W     9S-25W     9S-23W     9S-21W     9S-19W     9S-17W     9S-15W     9S-13W     9S-11W      9S-9W      9S-7W      9S-5W      9S-3W      9S-1W    11S-29W    11S-27W    11S-25W    11S-23W    11S-21W    11S-19W    11S-17W    11S-15W    11S-13W    11S-11W     11S-9W     11S-7W     11S-5W     11S-3W  \
1964-07-01  27.485451  31.030630  34.033219  33.324165  32.128648  31.062840  26.181291  20.321417  13.800362   9.759098   8.405950  10.863241  14.673105  17.850770  21.026174  31.718922  37.110915  39.668753  38.683976  36.627039  36.249138  33.116914  28.180135  21.366329  15.462535  11.759252  11.455130  13.322537  14.637281  16.949926  34.042473  39.462007  40.376354  39.757515  41.962364  46.779910  47.840255  44.462344  36.826621  28.028022  21.959280  18.620687  17.311268  17.224692  17.473408  34.033072  34.220023  32.467984  34.139274  41.011218  50.438577  58.322208  57.031921  49.300101  39.268944  32.739120  27.181060  23.943475  23.762576  23.520417  31.999062  26.913380  22.556817  25.235689  34.488984  46.113339  54.961532  58.180753  53.012546  43.930058  36.186323  32.035137  29.248761  29.427878  29.060110  28.539446  20.922954  16.584631  19.795201  27.932955  37.763739  46.933357  52.853855  49.739019  43.649742  36.472592  32.548425  31.187337  31.542511   
1964-08-01  25.134041  28.892213  32.244224  31.312138  28.023205  23.140009  19.731447  20.678491  21.145449  19.915070  17.140595  15.601282  16.977927  19.500000  23.858122  31.722705  36.623080  38.626416  35.558403  29.860509  23.306008  22.340322  24.424782  26.708800  27.261878  24.307406  20.023237  17.751901  18.529976  22.094569  44.055647  50.782871  54.061539  49.729267  39.785927  30.376471  29.302730  33.292942  38.550746  40.049969  36.362618  29.891805  23.085277  21.708293  23.700211  56.635325  66.638202  73.968439  70.277166  57.656656  42.441725  37.692705  42.143208  50.117562  55.030264  53.734533  44.308577  33.019388  27.872926  28.428859  64.803858  79.069716  90.069362  88.416571  74.868485  57.910707  47.638850  48.541220  58.942769  70.132803  73.105745  62.674476  49.021832  38.200524  33.165193  65.384478  81.007716  93.142901  95.223369  86.665160  71.924474  60.407450  56.964024  68.576672  83.846586  91.255356  82.553740  68.593659  52.127728   
1964-09-01  31.367659  34.122280  34.494202  31.541243  30.072745  29.333428  29.375670  29.461331  26.154350  22.014541  19.015783  17.692089  17.922611  20.608736  25.532724  38.997051  43.649513  43.931765  41.438267  38.415752  37.833583  37.792195  37.481729  33.360006  27.176460  20.645581  16.728718  15.754364  16.857639  21.411212  47.273037  54.336452  56.441828  53.966656  50.250771  48.626125  49.937261  51.590891  49.109775  41.243787  30.088702  21.973848  17.649079  17.535393  19.485892  53.968231  63.148476  67.282390  65.066889  61.131007  60.021663  63.812225  66.490977  64.895146  56.968851  45.353831  32.041379  23.528706  21.745114  22.243426  57.810207  66.525484  71.733953  70.729343  68.983041  69.838958  75.673641  77.287127  74.868485  69.430253  59.942806  46.032380  34.593786  29.954799  28.066528  58.255472  64.772371  70.028923  73.406403  75.515892  77.694916  81.550046  83.996726  82.458292  78.203964  70.355668  58.908743  50.448092  44.374092   
1964-10-01  34.375136  35.072069  35.284132

In [86]:
tn_pws_df.head()

27N-59W    27N-57W    27N-55W    27N-53W    27N-51W    27N-49W    27N-47W    27N-45W    27N-43W    27N-41W    27N-39W    27N-37W    27N-35W    27N-33W    27N-31W    27N-29W    27N-27W    27N-25W    27N-23W    27N-21W    27N-19W    27N-17W    25N-59W    25N-57W    25N-55W    25N-53W    25N-51W    25N-49W    25N-47W    25N-45W    25N-43W    25N-41W    25N-39W    25N-37W    25N-35W    25N-33W    25N-31W    25N-29W    25N-27W    25N-25W    25N-23W    25N-21W    25N-19W    25N-17W    23N-59W    23N-57W    23N-55W    23N-53W    23N-51W    23N-49W    23N-47W    23N-45W    23N-43W    23N-41W    23N-39W    23N-37W    23N-35W    23N-33W    23N-31W    23N-29W    23N-27W    23N-25W    23N-23W    23N-21W    23N-19W    23N-17W    21N-59W    21N-57W    21N-55W    21N-53W    21N-51W    21N-49W    21N-47W    21N-45W    21N-43W    21N-41W    21N-39W    21N-37W    21N-35W    21N-33W    21N-31W    21N-29W    21N-27W    21N-25W    21N-23W    21N-21W    21N-19W    21N-17W    19N-59W  \
1964-07-01  23.576471  23.433523  23.742788  23.436083  23.400855  23.568835  23.385679  24.758837  28.731342  33.217465  38.946373  45.060071  50.732632  56.257000  59.907679  61.729248  57.360003  54.223334  56.180513  61.494146  69.029342  71.331970  31.533633  33.559648  34.628312  35.300142  35.445733  36.168633  37.561683  39.588382  45.743306  51.138342  56.981488  62.658200  65.836920  66.850580  67.544504  65.046599  58.033180  52.559014  55.822934  62.541186  71.157572  75.700264  40.707862  43.601835  44.700112  45.508900  46.432101  48.027700  51.736641  54.282594  60.096589  66.296606  70.677083  73.594361  74.349714  72.782759  68.831533  65.816715  57.495130  50.806791  52.517807  58.223191  65.048059  70.698303  50.976956  51.618989  51.938521  52.317206  54.553460  58.084852  63.182039  66.456076  68.810246  71.877952  73.438478  71.846016  70.545446  68.597740  64.765577  60.742489  53.811244  48.492680  46.058441  47.181564  50.016397  52.013268  60.851623   
1964-08-01  11.322985  10.465180  10.235722   9.824968   9.219544   8.668333   8.572631   9.247702  10.751744  12.280065  13.036104  14.763468  17.962739  18.117671  15.241063  10.381233   6.688797   7.800000  15.980613  27.430275  38.417314  45.015553  18.952572  19.630843  20.600000  20.319941  19.791412  18.642425  18.631693  20.130822  22.568341  23.764048  24.542209  26.442579  29.585300  29.329337  26.580068  20.972363  16.686821  16.681727  25.181342  36.850644  47.594643  53.791914  31.100643  32.695718  33.833268  33.543554  33.353860  33.328966  34.491158  35.146124  35.521824  36.497123  37.481329  40.534553  43.982951  44.864240  42.283448  36.752823  30.871508  27.895878  33.677441  43.286603  52.325328  58.366172  44.174314  45.240800  45.497363  45.831212  47.555021  49.822987  51.442103  50.594071  48.046332  46.804807  48.249767  53.817655  57.384667  59.223053  57.476604  51.643489  42.363192  36.217399  37.696154  42.223808  47.914090  52.537606  53.245563   
1964-09-01  30.383219  27.906272  25.440322  24.066574  23.561409  23.810292  23.031283  21.440149  19.331322  18.013606  19.147062  24.440131  30.272925  35.403531  38.575122  39.012818  37.186019  34.839776  32.313619  30.619765  30.103986  30.384865  32.339604  30.046630  28.438179  28.327019  28.876461  29.400170  28.385384  26.404734  23.843028  22.357325  23.090258  26.545244  32.345943  38.283286  42.406250  43.370266  42.370981  41.281957  40.205721  40.396658  40.577087  40.085035  33.497761  31.812733  31.287857  32.447496  34.402326  36.040117  34.708644  32.951479  29.793456  27.776429  27.408940  30.736298  37.258690  43.713842  48.270074  50.263406  49.432884  47.504210  46.651902  45.957045  46.428116  46.106941  33.452055  32.449961  33.241691  35.867534  39.450729  42.273396  41.949017  41.125418  37.285922  33.105891  31.087136  35.510562  41.519393  48.027700  53.648486  55.881392  52.824710  48.885990  46.204978  43.435584  41.713907  41.005487  32.512152   
1964-10-01   5.554278   5.371220   6.00333

In [87]:
ts_pws_df.head()

5N-59W  5N-57W  5N-55W  5N-53W     5N-51W     5N-49W     5N-47W     5N-45W     5N-43W     5N-41W     5N-39W     5N-37W     5N-35W     5N-33W     5N-31W     5N-29W     5N-27W     5N-25W     5N-23W     5N-21W     5N-19W     5N-17W     5N-15W     5N-13W     5N-11W      5N-9W      5N-7W      5N-5W      5N-3W      5N-1W      5N-1E      5N-3E      5N-5E      5N-7E      5N-9E  5N-11E  5N-13E  5N-15E  3N-59W  3N-57W  3N-55W  3N-53W  3N-51W     3N-49W     3N-47W     3N-45W     3N-43W     3N-41W     3N-39W     3N-37W     3N-35W     3N-33W     3N-31W     3N-29W     3N-27W     3N-25W     3N-23W     3N-21W     3N-19W     3N-17W     3N-15W     3N-13W     3N-11W      3N-9W      3N-7W      3N-5W      3N-3W      3N-1W      3N-1E      3N-3E      3N-5E      3N-7E      3N-9E  3N-11E  3N-13E  3N-15E  1N-59W  1N-57W  1N-55W  1N-53W  1N-51W     1N-49W     1N-47W     1N-45W     1N-43W     1N-41W     1N-39W     1N-37W     1N-35W     1N-33W     1N-31W     1N-29W     1N-27W     1N-25W     1N-23W  \
1964-07-01     NaN     NaN     NaN     NaN   9.800510  10.692988  11.229426  11.280514  12.702756  14.402778  15.250246  17.755281  20.329781  21.781644  20.930361  20.497805  22.013178  24.960970  32.221887  39.658164  44.851979  43.793721  38.896015  33.003788  28.171084  24.946743  20.969025  17.910053  15.373028  16.347783  20.360010  25.279438  29.320471  30.852553  31.047383     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  15.454773  17.288725  19.159593  22.380572  24.177055  25.437178  26.802985  25.768974  23.726146  20.942302  19.523319  21.760744  25.684431  32.330326  38.438652  41.111799  38.583416  32.571460  26.534694  21.733154  19.702284  19.304145  18.906613  19.812370  21.044002  23.769729  28.219497  30.634131  31.973896  33.277320     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  22.583401  25.501569  29.279686  32.472142  33.952025  34.342394  32.203882  28.241813  23.583469  21.002143  21.653868  24.932910  28.435541  30.768328   
1964-08-01     NaN     NaN     NaN     NaN  15.902830  20.447494  23.405341  25.316003  28.708884  33.852769  39.408755  39.197066  33.057828  27.074896  25.700195  30.978218  40.477648  46.802778  50.800886  51.660527  49.545938  45.626856  41.556227  39.692065  37.702255  34.478109  28.032124  21.812382  18.595161  18.792818  21.779348  25.740629  29.783385  32.253062  34.047173     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  28.675076  32.249031  35.415957  39.940080  46.250189  51.600097  50.464740  41.769846  31.770584  27.070279  29.823648  36.179690  40.240527  42.311464  42.617485  41.047899  38.256241  35.058380  32.757595  29.705387  27.126555  24.300823  21.711748  21.585643  22.734335  24.644878  26.582701  27.910034  28.974817  29.634608     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  36.338547  41.099392  46.099024  52.162151  59.064202  64.015779  59.142709  47.589600  33.902950  25.850725  25.719448  29.565520  33.452205  34.148499   
1964-09-01     NaN     NaN     NaN     NaN  18.821530  21.733154  27.840977  33.032408  35.863770  35.328883  31.921466  30.183770  27.419154  28.733430  29.937602  30.331831  31.614079  31.672385  35.406920  39.256210  41.105231  38.093832  32.669558  27.472168  23.256182  20.787015  17.341569  13.729530  11.759677  13.793114  16.979988  20.001000  22.864164  24.124883  24.573360     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  29.213867  36.292699  43.472865  50.100399  53.501869  52.211589  45.190818  37.161943  32.300000  30.371203  30.594444  30.991934  30.731905  31.246440  32.829864  35.435858  36.002222  33.928896  29.942779  25.556604  22.507776  20.209156  17.973870  18.599462  20.663010  23.690715  26.822379  27.836128  28.091992  28.297350     NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  39.141410  45.078154  53.485793  62.583784  69.305267  69.856997  59.634302  46.405280  33.882887  27.821754  28.817529  29.706902  30.134698  27.882970   
1964-10-01     N

## Preprossessing data

In [88]:
### Removing NaN

In [89]:
atn_sst_df.dropna(axis=1, how='any',inplace=True)
ats_sst_df.dropna(axis=1, how='any', inplace=True)
tn_sst_df.dropna(axis=1, how='any', inplace=True)
ts_sst_df.dropna(axis=1, how='any', inplace=True)

atn_pws_df.dropna(axis=1, how='any', inplace=True)
ats_pws_df.dropna(axis=1, how='any', inplace=True)
tn_pws_df.dropna(axis=1, how='any', inplace=True)
ts_pws_df.dropna(axis=1, how='any', inplace=True)

In [90]:
## TODO: feature scaling

In [91]:
scaler = MinMaxScaler()

atn_sst_scaled_df = pd.DataFrame(scaler.fit_transform(atn_sst_df), columns=atn_sst_df.columns)
atn_sst_scaled_df.index = atn_sst_df.index

ats_sst_scaled_df = pd.DataFrame(scaler.fit_transform(ats_sst_df), columns=ats_sst_df.columns)
ats_sst_scaled_df.index = ats_sst_df.index

tn_sst_scaled_df = pd.DataFrame(scaler.fit_transform(tn_sst_df), columns=tn_sst_df.columns)
tn_sst_scaled_df.index = tn_sst_df.index

ts_sst_scaled_df = pd.DataFrame(scaler.fit_transform(ts_sst_df), columns=ts_sst_df.columns)
ts_sst_scaled_df.index = ts_sst_df.index

atn_pws_scaled_df = pd.DataFrame(scaler.fit_transform(atn_pws_df), columns=atn_pws_df.columns)
atn_pws_scaled_df.index = atn_pws_df.index

ats_pws_scaled_df = pd.DataFrame(scaler.fit_transform(ats_pws_df), columns=ats_pws_df.columns)
ats_pws_scaled_df.index = ats_pws_df.index

tn_pws_scaled_df = pd.DataFrame(scaler.fit_transform(tn_pws_df), columns=tn_pws_df.columns)
tn_pws_scaled_df.index = tn_pws_df.index

ts_pws_scaled_df = pd.DataFrame(scaler.fit_transform(ts_pws_df), columns=ts_pws_df.columns)
ts_pws_scaled_df.index = tn_pws_df.index

### Prepare data for ATN

In [92]:
atn_sst_transformed_df = create_transformed_df(atn_sst_scaled_df, "sst_")
atn_sst_transformed_df.head()

sst_19N-49W_7 sst_19N-49W_8 sst_19N-49W_9 sst_19N-49W_10 sst_19N-49W_11 sst_19N-49W_12 sst_19N-47W_7 sst_19N-47W_8 sst_19N-47W_9 sst_19N-47W_10 sst_19N-47W_11 sst_19N-47W_12 sst_19N-45W_7 sst_19N-45W_8 sst_19N-45W_9 sst_19N-45W_10 sst_19N-45W_11 sst_19N-45W_12 sst_19N-43W_7 sst_19N-43W_8 sst_19N-43W_9 sst_19N-43W_10 sst_19N-43W_11 sst_19N-43W_12 sst_19N-41W_7 sst_19N-41W_8 sst_19N-41W_9 sst_19N-41W_10 sst_19N-41W_11 sst_19N-41W_12 sst_19N-39W_7 sst_19N-39W_8 sst_19N-39W_9 sst_19N-39W_10 sst_19N-39W_11 sst_19N-39W_12 sst_19N-37W_7 sst_19N-37W_8 sst_19N-37W_9 sst_19N-37W_10 sst_19N-37W_11 sst_19N-37W_12 sst_19N-35W_7 sst_19N-35W_8 sst_19N-35W_9 sst_19N-35W_10 sst_19N-35W_11 sst_19N-35W_12 sst_19N-33W_7 sst_19N-33W_8 sst_19N-33W_9 sst_19N-33W_10 sst_19N-33W_11 sst_19N-33W_12 sst_19N-31W_7 sst_19N-31W_8 sst_19N-31W_9 sst_19N-31W_10 sst_19N-31W_11 sst_19N-31W_12 sst_19N-29W_7 sst_19N-29W_8 sst_19N-29W_9 sst_19N-29W_10 sst_19N-29W_11 sst_19N-29W_12 sst_19N-27W_7 sst_19N-27W_8  \
1973      0.930314      0.947735       0.95122       0.961672       0.933798       0.905923      0.916084      0.944056      0.947552       0.958042        0.93007       0.898601      0.915194      0.936396       0.95053       0.961131       0.936396       0.897527      0.911348      0.925532      0.950355       0.960993       0.939716       0.897163       0.90681      0.921147      0.956989       0.956989       0.942652       0.899642      0.902878      0.913669      0.956835       0.942446       0.935252       0.895683      0.891697      0.906137      0.949458       0.931408       0.927798       0.891697      0.883636      0.905455      0.938182       0.934545           0.92       0.887273      0.882784      0.908425      0.930403       0.945055       0.915751       0.882784      0.882353      0.911765      0.922794       0.948529       0.908088       0.878676      0.886861      0.908759      0.923358       0.937956       0.905109       0.872263      0.875912       0.89781   
1974      0.933798      0.940767      0.947735       0.944251       0.940767       0.919861      0.923077       0.93007      0.944056       0.940559       0.937063        0.91958      0.915194      0.925795      0.939929       0.943463       0.936396       0.915194      0.911348      0.925532      0.932624       0.943262       0.929078       0.900709      0.910394      0.924731      0.935484       0.946237       0.928315       0.892473      0.902878      0.920863      0.931655       0.938849       0.920863       0.892086      0.891697      0.909747      0.927798       0.927798       0.913357       0.877256      0.883636      0.894545          0.92       0.930909       0.905455       0.850909      0.879121      0.882784      0.912088       0.934066       0.904762       0.827839         0.875      0.889706      0.900735         0.9375       0.900735         0.8125      0.872263       0.90146       0.90146       0.930657        0.89781       0.813869      0.857664      0.908759   
1975      0.930314      0.958188      0.958188       0.944251       0.919861       0.898955      0.926573      0.954545      0.958042       0.944056       0.916084       0.898601      0.922261       0.95053      0.954064       0.946996       0.911661       0.897527      0.914894      0.939716      0.946809       0.946809       0.907801       0.893617      0.913978      0.935484      0.949821       0.942652       0.910394       0.896057      0.913669      0.928058       0.94964       0.938849       0.910072       0.895683      0.906137      0.920578      0.953069       0.927798       0.913357       0.891697      0.894545      0.912727      0.956364       0.927273       0.909091       0.883636      0.882784      0.912088      0.956044       0.930403       0.908425       0.882784      0.878676      0.915441      0.959559       0.941176       0.908088       0.882353      0.875912      0.919708      0.956204       0.945255        0.90146       0.890511      0.861314      0.916058   
1976      0.933798      0.958188 

In [93]:
atn_pws_transformed_df = create_transformed_df(atn_pws_scaled_df, "pws_")
atn_pws_transformed_df.head()

pws_19N-49W_7 pws_19N-49W_8 pws_19N-49W_9 pws_19N-49W_10 pws_19N-49W_11 pws_19N-49W_12 pws_19N-47W_7 pws_19N-47W_8 pws_19N-47W_9 pws_19N-47W_10 pws_19N-47W_11 pws_19N-47W_12 pws_19N-45W_7 pws_19N-45W_8 pws_19N-45W_9 pws_19N-45W_10 pws_19N-45W_11 pws_19N-45W_12 pws_19N-43W_7 pws_19N-43W_8 pws_19N-43W_9 pws_19N-43W_10 pws_19N-43W_11 pws_19N-43W_12 pws_19N-41W_7 pws_19N-41W_8 pws_19N-41W_9 pws_19N-41W_10 pws_19N-41W_11 pws_19N-41W_12 pws_19N-39W_7 pws_19N-39W_8 pws_19N-39W_9 pws_19N-39W_10 pws_19N-39W_11 pws_19N-39W_12 pws_19N-37W_7 pws_19N-37W_8 pws_19N-37W_9 pws_19N-37W_10 pws_19N-37W_11 pws_19N-37W_12 pws_19N-35W_7 pws_19N-35W_8 pws_19N-35W_9 pws_19N-35W_10 pws_19N-35W_11 pws_19N-35W_12 pws_19N-33W_7 pws_19N-33W_8 pws_19N-33W_9 pws_19N-33W_10 pws_19N-33W_11 pws_19N-33W_12 pws_19N-31W_7 pws_19N-31W_8 pws_19N-31W_9 pws_19N-31W_10 pws_19N-31W_11 pws_19N-31W_12 pws_19N-29W_7 pws_19N-29W_8 pws_19N-29W_9 pws_19N-29W_10 pws_19N-29W_11 pws_19N-29W_12 pws_19N-27W_7 pws_19N-27W_8  \
1973      0.470834      0.586423      0.456256        0.40176       0.255826       0.282037      0.495541      0.590628      0.458173       0.436046       0.286351        0.34457      0.435238      0.508718      0.397511       0.386132        0.24004       0.329673      0.390241      0.379544      0.324136       0.332288       0.156824       0.210768      0.491798      0.386482      0.383494         0.4185       0.174559       0.133529      0.529685      0.375245       0.39639       0.427591       0.179511      0.0296574      0.623895       0.47913      0.471912       0.423158        0.23024       0.103346      0.595065      0.508816      0.449713       0.350759       0.261391       0.218537      0.530648      0.497775      0.370299       0.294828       0.261317       0.251207       0.51597      0.530336        0.3499       0.314539       0.323194       0.319959       0.51247      0.549583       0.32764       0.365605        0.36319       0.359637      0.465948      0.453539   
1974      0.513238       0.64873      0.625709       0.289127       0.294428       0.245167      0.547391      0.610913      0.682916       0.296648        0.30867       0.276667      0.505851      0.489822      0.654255       0.239608       0.250726       0.251043      0.432769      0.339192      0.621193       0.206052       0.181027       0.241283      0.470667      0.311749      0.747186       0.319217       0.215875       0.347986      0.430058       0.26692       0.75204       0.408868        0.22618       0.391946      0.431467      0.380165      0.813453       0.543572       0.277858         0.4699      0.403549      0.432888      0.708049       0.538261       0.297956       0.470566      0.381261      0.474718      0.606159       0.485061       0.282536       0.431621      0.412914      0.555375      0.581938       0.487691       0.319815       0.440241      0.428707      0.603508       0.58312       0.519953       0.346248       0.463997      0.331349      0.461237   
1975      0.515659      0.550787      0.493251       0.566699       0.315988        0.11652      0.587123      0.584744      0.604486       0.527529       0.382322      0.0704343      0.573714      0.532094      0.598398       0.418127         0.3693        0.11416      0.527434      0.456123      0.507442       0.304227       0.303066       0.103839      0.633724      0.517292      0.535753       0.331907       0.312787       0.178991      0.621355      0.509006      0.465439       0.340128       0.252171       0.190169      0.686345      0.586194      0.478735       0.449158       0.246707        0.13876      0.622724      0.555925       0.43245       0.495542       0.269538      0.0824661      0.558361      0.481446      0.363529       0.478101       0.305964              0      0.540988      0.444015      0.330655        0.47878       0.394793              0      0.525971      0.405273       0.27082       0.479253       0.471914              0      0.416086      0.338108   
1976      0.505499      0.464863 

In [94]:
df_new = pd.concat([atn_sst_transformed_df, atn_pws_transformed_df], axis=1)
df_new.head()


sst_19N-49W_7 sst_19N-49W_8 sst_19N-49W_9 sst_19N-49W_10 sst_19N-49W_11 sst_19N-49W_12 sst_19N-47W_7 sst_19N-47W_8 sst_19N-47W_9 sst_19N-47W_10 sst_19N-47W_11 sst_19N-47W_12 sst_19N-45W_7 sst_19N-45W_8 sst_19N-45W_9 sst_19N-45W_10 sst_19N-45W_11 sst_19N-45W_12 sst_19N-43W_7 sst_19N-43W_8 sst_19N-43W_9 sst_19N-43W_10 sst_19N-43W_11 sst_19N-43W_12 sst_19N-41W_7 sst_19N-41W_8 sst_19N-41W_9 sst_19N-41W_10 sst_19N-41W_11 sst_19N-41W_12 sst_19N-39W_7 sst_19N-39W_8 sst_19N-39W_9 sst_19N-39W_10 sst_19N-39W_11 sst_19N-39W_12 sst_19N-37W_7 sst_19N-37W_8 sst_19N-37W_9 sst_19N-37W_10 sst_19N-37W_11 sst_19N-37W_12 sst_19N-35W_7 sst_19N-35W_8 sst_19N-35W_9 sst_19N-35W_10 sst_19N-35W_11 sst_19N-35W_12 sst_19N-33W_7 sst_19N-33W_8 sst_19N-33W_9 sst_19N-33W_10 sst_19N-33W_11 sst_19N-33W_12 sst_19N-31W_7 sst_19N-31W_8 sst_19N-31W_9 sst_19N-31W_10 sst_19N-31W_11 sst_19N-31W_12 sst_19N-29W_7 sst_19N-29W_8 sst_19N-29W_9 sst_19N-29W_10 sst_19N-29W_11 sst_19N-29W_12 sst_19N-27W_7 sst_19N-27W_8  \
1973      0.930314      0.947735       0.95122       0.961672       0.933798       0.905923      0.916084      0.944056      0.947552       0.958042        0.93007       0.898601      0.915194      0.936396       0.95053       0.961131       0.936396       0.897527      0.911348      0.925532      0.950355       0.960993       0.939716       0.897163       0.90681      0.921147      0.956989       0.956989       0.942652       0.899642      0.902878      0.913669      0.956835       0.942446       0.935252       0.895683      0.891697      0.906137      0.949458       0.931408       0.927798       0.891697      0.883636      0.905455      0.938182       0.934545           0.92       0.887273      0.882784      0.908425      0.930403       0.945055       0.915751       0.882784      0.882353      0.911765      0.922794       0.948529       0.908088       0.878676      0.886861      0.908759      0.923358       0.937956       0.905109       0.872263      0.875912       0.89781   
1974      0.933798      0.940767      0.947735       0.944251       0.940767       0.919861      0.923077       0.93007      0.944056       0.940559       0.937063        0.91958      0.915194      0.925795      0.939929       0.943463       0.936396       0.915194      0.911348      0.925532      0.932624       0.943262       0.929078       0.900709      0.910394      0.924731      0.935484       0.946237       0.928315       0.892473      0.902878      0.920863      0.931655       0.938849       0.920863       0.892086      0.891697      0.909747      0.927798       0.927798       0.913357       0.877256      0.883636      0.894545          0.92       0.930909       0.905455       0.850909      0.879121      0.882784      0.912088       0.934066       0.904762       0.827839         0.875      0.889706      0.900735         0.9375       0.900735         0.8125      0.872263       0.90146       0.90146       0.930657        0.89781       0.813869      0.857664      0.908759   
1975      0.930314      0.958188      0.958188       0.944251       0.919861       0.898955      0.926573      0.954545      0.958042       0.944056       0.916084       0.898601      0.922261       0.95053      0.954064       0.946996       0.911661       0.897527      0.914894      0.939716      0.946809       0.946809       0.907801       0.893617      0.913978      0.935484      0.949821       0.942652       0.910394       0.896057      0.913669      0.928058       0.94964       0.938849       0.910072       0.895683      0.906137      0.920578      0.953069       0.927798       0.913357       0.891697      0.894545      0.912727      0.956364       0.927273       0.909091       0.883636      0.882784      0.912088      0.956044       0.930403       0.908425       0.882784      0.878676      0.915441      0.959559       0.941176       0.908088       0.882353      0.875912      0.919708      0.956204       0.945255        0.90146       0.890511      0.861314      0.916058   
1976      0.933798      0.958188 

In [95]:
dataset_df = pd.concat([df_new, rainy_classified_df], axis=1)
dataset_df.head()

sst_19N-49W_7 sst_19N-49W_8 sst_19N-49W_9 sst_19N-49W_10 sst_19N-49W_11 sst_19N-49W_12 sst_19N-47W_7 sst_19N-47W_8 sst_19N-47W_9 sst_19N-47W_10 sst_19N-47W_11 sst_19N-47W_12 sst_19N-45W_7 sst_19N-45W_8 sst_19N-45W_9 sst_19N-45W_10 sst_19N-45W_11 sst_19N-45W_12 sst_19N-43W_7 sst_19N-43W_8 sst_19N-43W_9 sst_19N-43W_10 sst_19N-43W_11 sst_19N-43W_12 sst_19N-41W_7 sst_19N-41W_8 sst_19N-41W_9 sst_19N-41W_10 sst_19N-41W_11 sst_19N-41W_12 sst_19N-39W_7 sst_19N-39W_8 sst_19N-39W_9 sst_19N-39W_10 sst_19N-39W_11 sst_19N-39W_12 sst_19N-37W_7 sst_19N-37W_8 sst_19N-37W_9 sst_19N-37W_10 sst_19N-37W_11 sst_19N-37W_12 sst_19N-35W_7 sst_19N-35W_8 sst_19N-35W_9 sst_19N-35W_10 sst_19N-35W_11 sst_19N-35W_12 sst_19N-33W_7 sst_19N-33W_8 sst_19N-33W_9 sst_19N-33W_10 sst_19N-33W_11 sst_19N-33W_12 sst_19N-31W_7 sst_19N-31W_8 sst_19N-31W_9 sst_19N-31W_10 sst_19N-31W_11 sst_19N-31W_12 sst_19N-29W_7 sst_19N-29W_8 sst_19N-29W_9 sst_19N-29W_10 sst_19N-29W_11 sst_19N-29W_12 sst_19N-27W_7 sst_19N-27W_8  \
1973      0.930314      0.947735       0.95122       0.961672       0.933798       0.905923      0.916084      0.944056      0.947552       0.958042        0.93007       0.898601      0.915194      0.936396       0.95053       0.961131       0.936396       0.897527      0.911348      0.925532      0.950355       0.960993       0.939716       0.897163       0.90681      0.921147      0.956989       0.956989       0.942652       0.899642      0.902878      0.913669      0.956835       0.942446       0.935252       0.895683      0.891697      0.906137      0.949458       0.931408       0.927798       0.891697      0.883636      0.905455      0.938182       0.934545           0.92       0.887273      0.882784      0.908425      0.930403       0.945055       0.915751       0.882784      0.882353      0.911765      0.922794       0.948529       0.908088       0.878676      0.886861      0.908759      0.923358       0.937956       0.905109       0.872263      0.875912       0.89781   
1974      0.933798      0.940767      0.947735       0.944251       0.940767       0.919861      0.923077       0.93007      0.944056       0.940559       0.937063        0.91958      0.915194      0.925795      0.939929       0.943463       0.936396       0.915194      0.911348      0.925532      0.932624       0.943262       0.929078       0.900709      0.910394      0.924731      0.935484       0.946237       0.928315       0.892473      0.902878      0.920863      0.931655       0.938849       0.920863       0.892086      0.891697      0.909747      0.927798       0.927798       0.913357       0.877256      0.883636      0.894545          0.92       0.930909       0.905455       0.850909      0.879121      0.882784      0.912088       0.934066       0.904762       0.827839         0.875      0.889706      0.900735         0.9375       0.900735         0.8125      0.872263       0.90146       0.90146       0.930657        0.89781       0.813869      0.857664      0.908759   
1975      0.930314      0.958188      0.958188       0.944251       0.919861       0.898955      0.926573      0.954545      0.958042       0.944056       0.916084       0.898601      0.922261       0.95053      0.954064       0.946996       0.911661       0.897527      0.914894      0.939716      0.946809       0.946809       0.907801       0.893617      0.913978      0.935484      0.949821       0.942652       0.910394       0.896057      0.913669      0.928058       0.94964       0.938849       0.910072       0.895683      0.906137      0.920578      0.953069       0.927798       0.913357       0.891697      0.894545      0.912727      0.956364       0.927273       0.909091       0.883636      0.882784      0.912088      0.956044       0.930403       0.908425       0.882784      0.878676      0.915441      0.959559       0.941176       0.908088       0.882353      0.875912      0.919708      0.956204       0.945255        0.90146       0.890511      0.861314      0.916058   
1976      0.933798      0.958188 

In [96]:
#Removing 2017 due we don't have full 2018 available
dataset_df = dataset_df.loc['1973-01-01':'2016-12-01']

In [97]:
#Train
train_df = dataset_df.loc['1973-01-01':'2000-12-01']

test_df = dataset_df.loc['2000-01-01':'2016-12-01']

#Dropt last column to be the X values
feature_cols = dataset_df.columns
feature_cols=feature_cols.drop('classes')

# Input data(X)
X = train_df.loc[:, feature_cols]

# Output data(y)
y = train_df['classes']

X_test = test_df.loc[:, feature_cols]


### Testing classifiers for atn

In [98]:
new_pred_class = test_knn(X,y)

2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak


In [99]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [100]:
new_pred_class = test_svc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [101]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [102]:
new_pred_class = test_gpc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [103]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [104]:
new_pred_class = test_dtc(X,y)

2001 strong
2002 normal
2003 normal
2004 weak
2005 weak
2006 strong
2007 weak
2008 strong
2009 weak
2010 weak
2011 weak
2012 normal
2013 weak
2014 normal
2015 normal
2016 normal


In [105]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.4375

In [106]:
new_pred_class = test_rfc(X,y)

2001 normal
2002 normal
2003 weak
2004 normal
2005 normal
2006 normal
2007 normal
2008 normal
2009 weak
2010 normal
2011 weak
2012 normal
2013 normal
2014 normal
2015 weak
2016 normal


In [107]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.4375

In [108]:
new_pred_class = test_mlp(X,y)

2001 normal
2002 normal
2003 normal
2004 normal
2005 normal
2006 normal
2007 normal
2008 normal
2009 normal
2010 normal
2011 normal
2012 normal
2013 normal
2014 weak
2015 weak
2016 weak


In [109]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.375

In [110]:
new_pred_class = test_adc(X,y)

2001 weak
2002 normal
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 normal
2015 normal
2016 normal


In [111]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.6875

In [112]:
new_pred_class = test_gnb(X,y)

2001 normal
2002 weak
2003 weak
2004 normal
2005 normal
2006 normal
2007 weak
2008 normal
2009 weak
2010 weak
2011 normal
2012 normal
2013 normal
2014 weak
2015 weak
2016 weak


In [113]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.4375

### Prepare data for ATS

In [114]:
ats_sst_transformed_df = create_transformed_df(ats_sst_scaled_df, "sst_")
ats_sst_transformed_df.head()

sst_1S-29W_7 sst_1S-29W_8 sst_1S-29W_9 sst_1S-29W_10 sst_1S-29W_11 sst_1S-29W_12 sst_1S-27W_7 sst_1S-27W_8 sst_1S-27W_9 sst_1S-27W_10 sst_1S-27W_11 sst_1S-27W_12 sst_1S-25W_7 sst_1S-25W_8 sst_1S-25W_9 sst_1S-25W_10 sst_1S-25W_11 sst_1S-25W_12 sst_1S-23W_7 sst_1S-23W_8 sst_1S-23W_9 sst_1S-23W_10 sst_1S-23W_11 sst_1S-23W_12 sst_1S-21W_7 sst_1S-21W_8 sst_1S-21W_9 sst_1S-21W_10 sst_1S-21W_11 sst_1S-21W_12 sst_1S-19W_7 sst_1S-19W_8 sst_1S-19W_9 sst_1S-19W_10 sst_1S-19W_11 sst_1S-19W_12 sst_1S-17W_7 sst_1S-17W_8 sst_1S-17W_9 sst_1S-17W_10 sst_1S-17W_11 sst_1S-17W_12 sst_1S-15W_7 sst_1S-15W_8 sst_1S-15W_9 sst_1S-15W_10 sst_1S-15W_11 sst_1S-15W_12 sst_1S-13W_7 sst_1S-13W_8 sst_1S-13W_9 sst_1S-13W_10 sst_1S-13W_11 sst_1S-13W_12 sst_1S-11W_7 sst_1S-11W_8 sst_1S-11W_9 sst_1S-11W_10 sst_1S-11W_11 sst_1S-11W_12 sst_1S-9W_7 sst_1S-9W_8 sst_1S-9W_9 sst_1S-9W_10 sst_1S-9W_11 sst_1S-9W_12 sst_1S-7W_7 sst_1S-7W_8 sst_1S-7W_9 sst_1S-7W_10 sst_1S-7W_11 sst_1S-7W_12 sst_1S-5W_7 sst_1S-5W_8  \
1973     0.960714     0.967857     0.960714      0.971429      0.942857          0.95      0.98227     0.971631     0.968085      0.978723      0.953901      0.957447     0.967972     0.957295     0.953737      0.975089      0.964413      0.960854     0.946429     0.935714     0.935714         0.975      0.978571      0.967857     0.942238     0.935018     0.935018       0.98556       0.98556      0.971119     0.945455     0.938182     0.941818      0.985455      0.974545      0.967273     0.930909     0.930909     0.930909      0.963636      0.949091      0.956364     0.908088     0.908088     0.919118      0.948529      0.948529      0.963235     0.876812     0.884058     0.902174      0.927536      0.942029      0.971014     0.842294     0.867384     0.888889       0.90681      0.935484      0.964158        0.85    0.871429    0.889286     0.914286     0.942857     0.960714    0.862676    0.873239    0.894366     0.926056     0.947183     0.954225    0.888889       0.875   
1974     0.964286     0.935714     0.928571      0.932143      0.964286      0.953571     0.960993     0.939716     0.911348       0.93617      0.971631      0.964539     0.950178     0.921708     0.911032      0.935943      0.967972      0.953737     0.939286     0.903571     0.914286      0.935714      0.960714      0.939286     0.938628     0.906137     0.927798      0.949458      0.960289      0.938628     0.945455     0.916364     0.934545          0.96      0.956364      0.945455     0.934545     0.916364     0.916364      0.945455      0.938182      0.941818     0.908088     0.889706     0.882353      0.926471      0.930147      0.941176     0.873188     0.847826     0.844203      0.902174       0.92029      0.945652     0.845878     0.820789     0.827957       0.88172      0.910394      0.939068    0.846429    0.817857    0.842857     0.892857     0.914286     0.935714    0.852113    0.820423    0.852113     0.901408     0.911972     0.933099    0.868056    0.833333   
1975     0.928571     0.921429     0.910714      0.932143      0.953571      0.964286     0.929078      0.91844     0.914894      0.929078      0.960993      0.975177     0.932384     0.907473     0.896797      0.918149      0.967972      0.957295     0.935714     0.896429        0.875      0.914286      0.971429      0.928571     0.942238     0.898917     0.873646      0.927798      0.974729      0.920578     0.945455     0.912727     0.883636      0.941818      0.967273      0.930909     0.930909     0.905455         0.88      0.934545      0.941818      0.930909     0.893382        0.875     0.878676      0.919118        0.9375      0.933824     0.847826      0.82971     0.880435      0.887681      0.931159      0.938406     0.820789     0.802867     0.867384      0.863799      0.924731      0.939068    0.828571    0.803571    0.860714        0.875        0.925     0.939286    0.841549    0.809859    0.859155     0.883803     0.922535     0.940141    0.864583    0.833333   
1976     0.907143          0.9     0.

In [115]:
ats_pws_transformed_df = create_transformed_df(ats_pws_scaled_df, "pws_")
ats_pws_transformed_df.head()

pws_1S-29W_7 pws_1S-29W_8 pws_1S-29W_9 pws_1S-29W_10 pws_1S-29W_11 pws_1S-29W_12 pws_1S-27W_7 pws_1S-27W_8 pws_1S-27W_9 pws_1S-27W_10 pws_1S-27W_11 pws_1S-27W_12 pws_1S-25W_7 pws_1S-25W_8 pws_1S-25W_9 pws_1S-25W_10 pws_1S-25W_11 pws_1S-25W_12 pws_1S-23W_7 pws_1S-23W_8 pws_1S-23W_9 pws_1S-23W_10 pws_1S-23W_11 pws_1S-23W_12 pws_1S-21W_7 pws_1S-21W_8 pws_1S-21W_9 pws_1S-21W_10 pws_1S-21W_11 pws_1S-21W_12 pws_1S-19W_7 pws_1S-19W_8 pws_1S-19W_9 pws_1S-19W_10 pws_1S-19W_11 pws_1S-19W_12 pws_1S-17W_7 pws_1S-17W_8 pws_1S-17W_9 pws_1S-17W_10 pws_1S-17W_11 pws_1S-17W_12 pws_1S-15W_7 pws_1S-15W_8 pws_1S-15W_9 pws_1S-15W_10 pws_1S-15W_11 pws_1S-15W_12 pws_1S-13W_7 pws_1S-13W_8 pws_1S-13W_9 pws_1S-13W_10 pws_1S-13W_11 pws_1S-13W_12 pws_1S-11W_7 pws_1S-11W_8 pws_1S-11W_9 pws_1S-11W_10 pws_1S-11W_11 pws_1S-11W_12 pws_1S-9W_7 pws_1S-9W_8 pws_1S-9W_9 pws_1S-9W_10 pws_1S-9W_11 pws_1S-9W_12 pws_1S-7W_7 pws_1S-7W_8 pws_1S-7W_9 pws_1S-7W_10 pws_1S-7W_11 pws_1S-7W_12 pws_1S-5W_7 pws_1S-5W_8  \
1973     0.322986     0.198672     0.167726      0.205673      0.158418      0.158693     0.203968     0.221253     0.147649      0.212294      0.159888      0.128426     0.121216     0.251637     0.191647       0.25254      0.196768      0.142307    0.0906877     0.255753     0.260594      0.297694      0.246719      0.203837    0.0653876     0.201769     0.259012      0.266243       0.24562      0.219084    0.0723213      0.18604     0.252631      0.240682      0.245364      0.237692            0     0.168131     0.230428      0.234104      0.215103      0.240245            0     0.185734       0.2332      0.257598      0.198168      0.226247    0.0160496     0.212905     0.249878      0.304577       0.23772      0.233636    0.0892415     0.278848     0.293104       0.35931       0.33472      0.271522    0.159274    0.339722    0.317565     0.395395     0.428027      0.29748    0.268979    0.426509    0.349491     0.497293     0.536321     0.296284    0.376105    0.498263   
1974      0.15918     0.267603      0.33704      0.176994       0.30068     0.0463691     0.116556     0.261323     0.260738      0.115916      0.268856      0.108217     0.113813     0.277736      0.24218      0.145048      0.293671       0.18927     0.165859     0.277798      0.28041      0.209433      0.343403      0.265775     0.202034      0.21754     0.300294      0.226349       0.32876      0.255685     0.229699     0.180014     0.321801      0.237041      0.317409      0.227385      0.22365     0.106415     0.343766      0.220035      0.287634      0.149131     0.189994    0.0925961     0.307442       0.21361      0.233811      0.105563     0.159639     0.103061     0.266151      0.233829      0.251757      0.133614     0.180048     0.160871     0.269259      0.285506      0.341709       0.21828    0.230078    0.197652    0.285833      0.32184     0.426746     0.285046    0.291866    0.225748     0.30373     0.394288     0.455768     0.353047    0.345771    0.256142   
1975     0.127049     0.310173     0.212412      0.285477      0.213701       0.27526     0.073895     0.240143      0.11535      0.239372      0.177323      0.221585    0.0796402     0.213808    0.0655053      0.203126      0.189823      0.198072     0.144903     0.237439    0.0590007      0.192286      0.224857      0.215526     0.156668     0.239359    0.0618054      0.189233      0.187121      0.228693     0.159642     0.262294    0.0935446       0.24767      0.144869      0.274139     0.130845     0.263148    0.0975196      0.286441     0.0796698      0.322591     0.156731     0.213819     0.134218      0.286072     0.0930494      0.318705     0.178017      0.14285     0.122387      0.288639        0.1666      0.316237     0.219454     0.116046     0.144644       0.33026      0.280589      0.354077    0.236714    0.120507    0.168657     0.386053      0.36807     0.385119    0.263598    0.119632    0.200398     0.438417      0.47237     0.403245     0.30747    0.118203   
1976     0.078585     0.404422     0.

In [116]:
df_new = pd.concat([ats_sst_transformed_df, ats_pws_transformed_df], axis=1)
df_new.head()


sst_1S-29W_7 sst_1S-29W_8 sst_1S-29W_9 sst_1S-29W_10 sst_1S-29W_11 sst_1S-29W_12 sst_1S-27W_7 sst_1S-27W_8 sst_1S-27W_9 sst_1S-27W_10 sst_1S-27W_11 sst_1S-27W_12 sst_1S-25W_7 sst_1S-25W_8 sst_1S-25W_9 sst_1S-25W_10 sst_1S-25W_11 sst_1S-25W_12 sst_1S-23W_7 sst_1S-23W_8 sst_1S-23W_9 sst_1S-23W_10 sst_1S-23W_11 sst_1S-23W_12 sst_1S-21W_7 sst_1S-21W_8 sst_1S-21W_9 sst_1S-21W_10 sst_1S-21W_11 sst_1S-21W_12 sst_1S-19W_7 sst_1S-19W_8 sst_1S-19W_9 sst_1S-19W_10 sst_1S-19W_11 sst_1S-19W_12 sst_1S-17W_7 sst_1S-17W_8 sst_1S-17W_9 sst_1S-17W_10 sst_1S-17W_11 sst_1S-17W_12 sst_1S-15W_7 sst_1S-15W_8 sst_1S-15W_9 sst_1S-15W_10 sst_1S-15W_11 sst_1S-15W_12 sst_1S-13W_7 sst_1S-13W_8 sst_1S-13W_9 sst_1S-13W_10 sst_1S-13W_11 sst_1S-13W_12 sst_1S-11W_7 sst_1S-11W_8 sst_1S-11W_9 sst_1S-11W_10 sst_1S-11W_11 sst_1S-11W_12 sst_1S-9W_7 sst_1S-9W_8 sst_1S-9W_9 sst_1S-9W_10 sst_1S-9W_11 sst_1S-9W_12 sst_1S-7W_7 sst_1S-7W_8 sst_1S-7W_9 sst_1S-7W_10 sst_1S-7W_11 sst_1S-7W_12 sst_1S-5W_7 sst_1S-5W_8  \
1973     0.960714     0.967857     0.960714      0.971429      0.942857          0.95      0.98227     0.971631     0.968085      0.978723      0.953901      0.957447     0.967972     0.957295     0.953737      0.975089      0.964413      0.960854     0.946429     0.935714     0.935714         0.975      0.978571      0.967857     0.942238     0.935018     0.935018       0.98556       0.98556      0.971119     0.945455     0.938182     0.941818      0.985455      0.974545      0.967273     0.930909     0.930909     0.930909      0.963636      0.949091      0.956364     0.908088     0.908088     0.919118      0.948529      0.948529      0.963235     0.876812     0.884058     0.902174      0.927536      0.942029      0.971014     0.842294     0.867384     0.888889       0.90681      0.935484      0.964158        0.85    0.871429    0.889286     0.914286     0.942857     0.960714    0.862676    0.873239    0.894366     0.926056     0.947183     0.954225    0.888889       0.875   
1974     0.964286     0.935714     0.928571      0.932143      0.964286      0.953571     0.960993     0.939716     0.911348       0.93617      0.971631      0.964539     0.950178     0.921708     0.911032      0.935943      0.967972      0.953737     0.939286     0.903571     0.914286      0.935714      0.960714      0.939286     0.938628     0.906137     0.927798      0.949458      0.960289      0.938628     0.945455     0.916364     0.934545          0.96      0.956364      0.945455     0.934545     0.916364     0.916364      0.945455      0.938182      0.941818     0.908088     0.889706     0.882353      0.926471      0.930147      0.941176     0.873188     0.847826     0.844203      0.902174       0.92029      0.945652     0.845878     0.820789     0.827957       0.88172      0.910394      0.939068    0.846429    0.817857    0.842857     0.892857     0.914286     0.935714    0.852113    0.820423    0.852113     0.901408     0.911972     0.933099    0.868056    0.833333   
1975     0.928571     0.921429     0.910714      0.932143      0.953571      0.964286     0.929078      0.91844     0.914894      0.929078      0.960993      0.975177     0.932384     0.907473     0.896797      0.918149      0.967972      0.957295     0.935714     0.896429        0.875      0.914286      0.971429      0.928571     0.942238     0.898917     0.873646      0.927798      0.974729      0.920578     0.945455     0.912727     0.883636      0.941818      0.967273      0.930909     0.930909     0.905455         0.88      0.934545      0.941818      0.930909     0.893382        0.875     0.878676      0.919118        0.9375      0.933824     0.847826      0.82971     0.880435      0.887681      0.931159      0.938406     0.820789     0.802867     0.867384      0.863799      0.924731      0.939068    0.828571    0.803571    0.860714        0.875        0.925     0.939286    0.841549    0.809859    0.859155     0.883803     0.922535     0.940141    0.864583    0.833333   
1976     0.907143          0.9     0.

In [117]:
dataset_df = pd.concat([df_new, rainy_classified_df], axis=1)
dataset_df.head()

sst_1S-29W_7 sst_1S-29W_8 sst_1S-29W_9 sst_1S-29W_10 sst_1S-29W_11 sst_1S-29W_12 sst_1S-27W_7 sst_1S-27W_8 sst_1S-27W_9 sst_1S-27W_10 sst_1S-27W_11 sst_1S-27W_12 sst_1S-25W_7 sst_1S-25W_8 sst_1S-25W_9 sst_1S-25W_10 sst_1S-25W_11 sst_1S-25W_12 sst_1S-23W_7 sst_1S-23W_8 sst_1S-23W_9 sst_1S-23W_10 sst_1S-23W_11 sst_1S-23W_12 sst_1S-21W_7 sst_1S-21W_8 sst_1S-21W_9 sst_1S-21W_10 sst_1S-21W_11 sst_1S-21W_12 sst_1S-19W_7 sst_1S-19W_8 sst_1S-19W_9 sst_1S-19W_10 sst_1S-19W_11 sst_1S-19W_12 sst_1S-17W_7 sst_1S-17W_8 sst_1S-17W_9 sst_1S-17W_10 sst_1S-17W_11 sst_1S-17W_12 sst_1S-15W_7 sst_1S-15W_8 sst_1S-15W_9 sst_1S-15W_10 sst_1S-15W_11 sst_1S-15W_12 sst_1S-13W_7 sst_1S-13W_8 sst_1S-13W_9 sst_1S-13W_10 sst_1S-13W_11 sst_1S-13W_12 sst_1S-11W_7 sst_1S-11W_8 sst_1S-11W_9 sst_1S-11W_10 sst_1S-11W_11 sst_1S-11W_12 sst_1S-9W_7 sst_1S-9W_8 sst_1S-9W_9 sst_1S-9W_10 sst_1S-9W_11 sst_1S-9W_12 sst_1S-7W_7 sst_1S-7W_8 sst_1S-7W_9 sst_1S-7W_10 sst_1S-7W_11 sst_1S-7W_12 sst_1S-5W_7 sst_1S-5W_8  \
1973     0.960714     0.967857     0.960714      0.971429      0.942857          0.95      0.98227     0.971631     0.968085      0.978723      0.953901      0.957447     0.967972     0.957295     0.953737      0.975089      0.964413      0.960854     0.946429     0.935714     0.935714         0.975      0.978571      0.967857     0.942238     0.935018     0.935018       0.98556       0.98556      0.971119     0.945455     0.938182     0.941818      0.985455      0.974545      0.967273     0.930909     0.930909     0.930909      0.963636      0.949091      0.956364     0.908088     0.908088     0.919118      0.948529      0.948529      0.963235     0.876812     0.884058     0.902174      0.927536      0.942029      0.971014     0.842294     0.867384     0.888889       0.90681      0.935484      0.964158        0.85    0.871429    0.889286     0.914286     0.942857     0.960714    0.862676    0.873239    0.894366     0.926056     0.947183     0.954225    0.888889       0.875   
1974     0.964286     0.935714     0.928571      0.932143      0.964286      0.953571     0.960993     0.939716     0.911348       0.93617      0.971631      0.964539     0.950178     0.921708     0.911032      0.935943      0.967972      0.953737     0.939286     0.903571     0.914286      0.935714      0.960714      0.939286     0.938628     0.906137     0.927798      0.949458      0.960289      0.938628     0.945455     0.916364     0.934545          0.96      0.956364      0.945455     0.934545     0.916364     0.916364      0.945455      0.938182      0.941818     0.908088     0.889706     0.882353      0.926471      0.930147      0.941176     0.873188     0.847826     0.844203      0.902174       0.92029      0.945652     0.845878     0.820789     0.827957       0.88172      0.910394      0.939068    0.846429    0.817857    0.842857     0.892857     0.914286     0.935714    0.852113    0.820423    0.852113     0.901408     0.911972     0.933099    0.868056    0.833333   
1975     0.928571     0.921429     0.910714      0.932143      0.953571      0.964286     0.929078      0.91844     0.914894      0.929078      0.960993      0.975177     0.932384     0.907473     0.896797      0.918149      0.967972      0.957295     0.935714     0.896429        0.875      0.914286      0.971429      0.928571     0.942238     0.898917     0.873646      0.927798      0.974729      0.920578     0.945455     0.912727     0.883636      0.941818      0.967273      0.930909     0.930909     0.905455         0.88      0.934545      0.941818      0.930909     0.893382        0.875     0.878676      0.919118        0.9375      0.933824     0.847826      0.82971     0.880435      0.887681      0.931159      0.938406     0.820789     0.802867     0.867384      0.863799      0.924731      0.939068    0.828571    0.803571    0.860714        0.875        0.925     0.939286    0.841549    0.809859    0.859155     0.883803     0.922535     0.940141    0.864583    0.833333   
1976     0.907143          0.9     0.

In [118]:
#Removing 2017 due we don't have full 2018 available
dataset_df = dataset_df.loc['1973-01-01':'2016-12-01']

In [119]:
#Train
train_df = dataset_df.loc['1973-01-01':'2000-12-01']

test_df = dataset_df.loc['2000-01-01':'2016-12-01']

#Dropt last column to be the X values
feature_cols = dataset_df.columns
feature_cols=feature_cols.drop('classes')

# Input data(X)
X = train_df.loc[:, feature_cols]

# Output data(y)
y = train_df['classes']

X_test = test_df.loc[:, feature_cols]


### Testing classifiers for ats

In [120]:
new_pred_class = test_knn(X,y)

2001 weak
2001 weak
2001 normal
2001 normal
2001 weak
2001 weak
2001 weak
2001 weak
2001 normal
2001 normal
2001 weak
2001 normal
2001 weak
2001 weak
2001 weak
2001 weak


In [121]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5

In [122]:
new_pred_class = test_svc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [123]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [124]:
new_pred_class = test_gpc(X,y)

2001 weak
2002 normal
2003 weak
2004 weak
2005 weak
2006 normal
2007 weak
2008 weak
2009 normal
2010 normal
2011 weak
2012 normal
2013 weak
2014 weak
2015 weak
2016 weak


In [125]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.625

In [126]:
new_pred_class = test_dtc(X,y)

2001 weak
2002 normal
2003 normal
2004 weak
2005 weak
2006 weak
2007 weak
2008 normal
2009 normal
2010 normal
2011 normal
2012 normal
2013 normal
2014 weak
2015 normal
2016 normal


In [127]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.4375

In [128]:
new_pred_class = test_rfc(X,y)

2001 normal
2002 weak
2003 weak
2004 weak
2005 weak
2006 normal
2007 normal
2008 normal
2009 normal
2010 normal
2011 normal
2012 normal
2013 normal
2014 weak
2015 weak
2016 weak


In [129]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5

In [130]:
new_pred_class = test_mlp(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [131]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [132]:
new_pred_class = test_adc(X,y)

2001 weak
2002 weak
2003 normal
2004 weak
2005 weak
2006 weak
2007 weak
2008 normal
2009 normal
2010 normal
2011 weak
2012 normal
2013 normal
2014 weak
2015 normal
2016 weak


In [133]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5

In [134]:
new_pred_class = test_gnb(X,y)

2001 weak
2002 weak
2003 normal
2004 normal
2005 weak
2006 normal
2007 weak
2008 weak
2009 normal
2010 normal
2011 weak
2012 normal
2013 weak
2014 weak
2015 weak
2016 weak


In [135]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.4375

# AFTER 1


### Prepare data for TN

In [136]:
tn_sst_transformed_df = create_transformed_df(tn_sst_scaled_df, "sst_")
tn_sst_transformed_df.head()

sst_27N-59W_7 sst_27N-59W_8 sst_27N-59W_9 sst_27N-59W_10 sst_27N-59W_11 sst_27N-59W_12 sst_27N-57W_7 sst_27N-57W_8 sst_27N-57W_9 sst_27N-57W_10 sst_27N-57W_11 sst_27N-57W_12 sst_27N-55W_7 sst_27N-55W_8 sst_27N-55W_9 sst_27N-55W_10 sst_27N-55W_11 sst_27N-55W_12 sst_27N-53W_7 sst_27N-53W_8 sst_27N-53W_9 sst_27N-53W_10 sst_27N-53W_11 sst_27N-53W_12 sst_27N-51W_7 sst_27N-51W_8 sst_27N-51W_9 sst_27N-51W_10 sst_27N-51W_11 sst_27N-51W_12 sst_27N-49W_7 sst_27N-49W_8 sst_27N-49W_9 sst_27N-49W_10 sst_27N-49W_11 sst_27N-49W_12 sst_27N-47W_7 sst_27N-47W_8 sst_27N-47W_9 sst_27N-47W_10 sst_27N-47W_11 sst_27N-47W_12 sst_27N-45W_7 sst_27N-45W_8 sst_27N-45W_9 sst_27N-45W_10 sst_27N-45W_11 sst_27N-45W_12 sst_27N-43W_7 sst_27N-43W_8 sst_27N-43W_9 sst_27N-43W_10 sst_27N-43W_11 sst_27N-43W_12 sst_27N-41W_7 sst_27N-41W_8 sst_27N-41W_9 sst_27N-41W_10 sst_27N-41W_11 sst_27N-41W_12 sst_27N-39W_7 sst_27N-39W_8 sst_27N-39W_9 sst_27N-39W_10 sst_27N-39W_11 sst_27N-39W_12 sst_27N-37W_7 sst_27N-37W_8  \
1973      0.924658      0.955479      0.972603       0.928082       0.883562        0.80137      0.920139      0.954861       0.96875       0.927083       0.881944       0.798611      0.912587      0.947552      0.961538       0.923077       0.877622       0.793706      0.908451      0.943662      0.957746       0.922535       0.876761       0.799296      0.904594      0.939929       0.95053       0.922261       0.876325        0.80212       0.90106      0.932862       0.95053       0.922261       0.876325       0.805654      0.897527      0.925795      0.946996       0.922261       0.876325       0.809187      0.901408      0.926056      0.947183       0.926056       0.883803        0.81338      0.900709      0.925532      0.950355       0.929078       0.886525       0.815603      0.893238      0.914591      0.946619       0.925267       0.882562       0.818505      0.891697      0.913357      0.945848       0.927798       0.873646       0.826715      0.886029      0.911765   
1974      0.934932       0.94863       0.94863       0.907534       0.869863       0.811644      0.930556      0.944444      0.947917        0.90625       0.868056         0.8125      0.923077      0.940559      0.944056       0.905594       0.867133       0.818182      0.919014       0.93662      0.940141       0.908451       0.866197       0.823944      0.918728      0.932862      0.939929       0.908127       0.865724       0.826855      0.922261      0.932862      0.939929       0.908127       0.865724       0.823322      0.918728      0.929329      0.936396       0.908127       0.865724       0.819788      0.911972      0.926056      0.926056       0.908451       0.869718       0.827465      0.897163      0.921986      0.911348       0.904255       0.875887       0.829787      0.879004      0.914591      0.900356       0.900356       0.879004       0.829181      0.877256      0.916968      0.898917       0.902527       0.884477       0.826715      0.878676      0.922794   
1975      0.917808      0.958904      0.969178       0.931507       0.886986       0.797945      0.916667      0.961806       0.96875       0.930556       0.885417       0.795139      0.916084      0.961538      0.965035       0.926573       0.881119       0.793706      0.922535      0.964789      0.964789       0.929577       0.883803       0.799296      0.922261      0.964664      0.957597       0.925795       0.883392       0.798587      0.925795      0.961131       0.95053       0.918728       0.879859        0.80212      0.922261      0.957597      0.943463       0.911661       0.872792        0.80212      0.919014      0.961268      0.947183       0.911972       0.873239       0.806338      0.911348      0.957447      0.950355       0.911348        0.87234       0.808511      0.907473      0.953737      0.950178       0.907473       0.868327       0.807829      0.906137      0.949458      0.956679       0.913357       0.873646       0.819495      0.908088      0.948529   
1976      0.934932       0.94863 

In [137]:
tn_pws_transformed_df = create_transformed_df(tn_pws_scaled_df, "pws_")
tn_pws_transformed_df.head()

pws_27N-59W_7 pws_27N-59W_8 pws_27N-59W_9 pws_27N-59W_10 pws_27N-59W_11 pws_27N-59W_12 pws_27N-57W_7 pws_27N-57W_8 pws_27N-57W_9 pws_27N-57W_10 pws_27N-57W_11 pws_27N-57W_12 pws_27N-55W_7 pws_27N-55W_8 pws_27N-55W_9 pws_27N-55W_10 pws_27N-55W_11 pws_27N-55W_12 pws_27N-53W_7 pws_27N-53W_8 pws_27N-53W_9 pws_27N-53W_10 pws_27N-53W_11 pws_27N-53W_12 pws_27N-51W_7 pws_27N-51W_8 pws_27N-51W_9 pws_27N-51W_10 pws_27N-51W_11 pws_27N-51W_12 pws_27N-49W_7 pws_27N-49W_8 pws_27N-49W_9 pws_27N-49W_10 pws_27N-49W_11 pws_27N-49W_12 pws_27N-47W_7 pws_27N-47W_8 pws_27N-47W_9 pws_27N-47W_10 pws_27N-47W_11 pws_27N-47W_12 pws_27N-45W_7 pws_27N-45W_8 pws_27N-45W_9 pws_27N-45W_10 pws_27N-45W_11 pws_27N-45W_12 pws_27N-43W_7 pws_27N-43W_8 pws_27N-43W_9 pws_27N-43W_10 pws_27N-43W_11 pws_27N-43W_12 pws_27N-41W_7 pws_27N-41W_8 pws_27N-41W_9 pws_27N-41W_10 pws_27N-41W_11 pws_27N-41W_12 pws_27N-39W_7 pws_27N-39W_8 pws_27N-39W_9 pws_27N-39W_10 pws_27N-39W_11 pws_27N-39W_12 pws_27N-37W_7 pws_27N-37W_8  \
1973      0.141991      0.202282      0.182834       0.140431       0.130595       0.408164      0.224189      0.243587      0.197455       0.136505       0.140419       0.497815      0.270266       0.25027       0.17416       0.111014       0.124275       0.490577      0.350979      0.286412      0.151319      0.0937724      0.0824603       0.531783      0.405526      0.312858      0.112903      0.0839912      0.0399059       0.532587      0.405133      0.310053     0.0693838      0.0834919      0.0163269       0.486564       0.40073      0.355827      0.110037       0.127282      0.0537252       0.493543      0.350376      0.347112      0.129269       0.137701      0.0585415        0.45474      0.281726      0.322024       0.15259       0.138767      0.0460323       0.413312       0.19838      0.252626      0.148612       0.123977      0.0294338       0.296446       0.18459      0.229289      0.154626       0.135429      0.0139513       0.225876      0.280309      0.250694   
1974      0.115838      0.281891      0.373926      0.0651451       0.135841       0.218599      0.172336      0.300119       0.47943       0.125158      0.0524175       0.196284      0.206399      0.275448      0.476283       0.177567      0.0516935       0.132965      0.265148      0.301217      0.533123       0.248521        0.10413      0.0773601      0.321291      0.326983      0.577232       0.299805       0.126679      0.0892882      0.341976      0.339988      0.582882       0.307722       0.100379       0.131045      0.396691      0.375983      0.562303       0.314129       0.141487       0.204286      0.402364      0.362908      0.479616       0.279704       0.177453         0.2366      0.381296      0.357646      0.399679       0.266226       0.132808       0.242156      0.302303      0.307684      0.297561       0.233339      0.0653924       0.196614      0.288115      0.309723      0.282703       0.238928      0.0313411       0.177126      0.402051      0.349377   
1975       0.26191     0.0132205      0.131091       0.191625       0.189988       0.723114      0.338014    0.00573644      0.179527       0.276051       0.250185              1      0.346488     0.0208399      0.217489       0.291591       0.259406              1      0.372149     0.0480113      0.282666       0.278641       0.277827              1       0.37704     0.0925395      0.341447       0.225196       0.273177       0.858204      0.349013      0.117747      0.354135       0.135377        0.24485        0.62097      0.357313      0.155263      0.366666       0.115709       0.285052       0.490006      0.326432      0.159481      0.350376      0.0934271       0.261206       0.353958      0.314373      0.182754      0.342731      0.0926516       0.220174       0.293753      0.271645      0.183113      0.281955      0.0783058       0.142605       0.227064      0.277918      0.209387      0.266902      0.0727482      0.0911853       0.185508      0.359823      0.265141   
1976     0.0379741      0.159136 

In [138]:
df_new = pd.concat([tn_sst_transformed_df, tn_pws_transformed_df], axis=1)
df_new.head()


sst_27N-59W_7 sst_27N-59W_8 sst_27N-59W_9 sst_27N-59W_10 sst_27N-59W_11 sst_27N-59W_12 sst_27N-57W_7 sst_27N-57W_8 sst_27N-57W_9 sst_27N-57W_10 sst_27N-57W_11 sst_27N-57W_12 sst_27N-55W_7 sst_27N-55W_8 sst_27N-55W_9 sst_27N-55W_10 sst_27N-55W_11 sst_27N-55W_12 sst_27N-53W_7 sst_27N-53W_8 sst_27N-53W_9 sst_27N-53W_10 sst_27N-53W_11 sst_27N-53W_12 sst_27N-51W_7 sst_27N-51W_8 sst_27N-51W_9 sst_27N-51W_10 sst_27N-51W_11 sst_27N-51W_12 sst_27N-49W_7 sst_27N-49W_8 sst_27N-49W_9 sst_27N-49W_10 sst_27N-49W_11 sst_27N-49W_12 sst_27N-47W_7 sst_27N-47W_8 sst_27N-47W_9 sst_27N-47W_10 sst_27N-47W_11 sst_27N-47W_12 sst_27N-45W_7 sst_27N-45W_8 sst_27N-45W_9 sst_27N-45W_10 sst_27N-45W_11 sst_27N-45W_12 sst_27N-43W_7 sst_27N-43W_8 sst_27N-43W_9 sst_27N-43W_10 sst_27N-43W_11 sst_27N-43W_12 sst_27N-41W_7 sst_27N-41W_8 sst_27N-41W_9 sst_27N-41W_10 sst_27N-41W_11 sst_27N-41W_12 sst_27N-39W_7 sst_27N-39W_8 sst_27N-39W_9 sst_27N-39W_10 sst_27N-39W_11 sst_27N-39W_12 sst_27N-37W_7 sst_27N-37W_8  \
1973      0.924658      0.955479      0.972603       0.928082       0.883562        0.80137      0.920139      0.954861       0.96875       0.927083       0.881944       0.798611      0.912587      0.947552      0.961538       0.923077       0.877622       0.793706      0.908451      0.943662      0.957746       0.922535       0.876761       0.799296      0.904594      0.939929       0.95053       0.922261       0.876325        0.80212       0.90106      0.932862       0.95053       0.922261       0.876325       0.805654      0.897527      0.925795      0.946996       0.922261       0.876325       0.809187      0.901408      0.926056      0.947183       0.926056       0.883803        0.81338      0.900709      0.925532      0.950355       0.929078       0.886525       0.815603      0.893238      0.914591      0.946619       0.925267       0.882562       0.818505      0.891697      0.913357      0.945848       0.927798       0.873646       0.826715      0.886029      0.911765   
1974      0.934932       0.94863       0.94863       0.907534       0.869863       0.811644      0.930556      0.944444      0.947917        0.90625       0.868056         0.8125      0.923077      0.940559      0.944056       0.905594       0.867133       0.818182      0.919014       0.93662      0.940141       0.908451       0.866197       0.823944      0.918728      0.932862      0.939929       0.908127       0.865724       0.826855      0.922261      0.932862      0.939929       0.908127       0.865724       0.823322      0.918728      0.929329      0.936396       0.908127       0.865724       0.819788      0.911972      0.926056      0.926056       0.908451       0.869718       0.827465      0.897163      0.921986      0.911348       0.904255       0.875887       0.829787      0.879004      0.914591      0.900356       0.900356       0.879004       0.829181      0.877256      0.916968      0.898917       0.902527       0.884477       0.826715      0.878676      0.922794   
1975      0.917808      0.958904      0.969178       0.931507       0.886986       0.797945      0.916667      0.961806       0.96875       0.930556       0.885417       0.795139      0.916084      0.961538      0.965035       0.926573       0.881119       0.793706      0.922535      0.964789      0.964789       0.929577       0.883803       0.799296      0.922261      0.964664      0.957597       0.925795       0.883392       0.798587      0.925795      0.961131       0.95053       0.918728       0.879859        0.80212      0.922261      0.957597      0.943463       0.911661       0.872792        0.80212      0.919014      0.961268      0.947183       0.911972       0.873239       0.806338      0.911348      0.957447      0.950355       0.911348        0.87234       0.808511      0.907473      0.953737      0.950178       0.907473       0.868327       0.807829      0.906137      0.949458      0.956679       0.913357       0.873646       0.819495      0.908088      0.948529   
1976      0.934932       0.94863 

In [139]:
dataset_df = pd.concat([df_new, rainy_classified_df], axis=1)
dataset_df.head()

sst_27N-59W_7 sst_27N-59W_8 sst_27N-59W_9 sst_27N-59W_10 sst_27N-59W_11 sst_27N-59W_12 sst_27N-57W_7 sst_27N-57W_8 sst_27N-57W_9 sst_27N-57W_10 sst_27N-57W_11 sst_27N-57W_12 sst_27N-55W_7 sst_27N-55W_8 sst_27N-55W_9 sst_27N-55W_10 sst_27N-55W_11 sst_27N-55W_12 sst_27N-53W_7 sst_27N-53W_8 sst_27N-53W_9 sst_27N-53W_10 sst_27N-53W_11 sst_27N-53W_12 sst_27N-51W_7 sst_27N-51W_8 sst_27N-51W_9 sst_27N-51W_10 sst_27N-51W_11 sst_27N-51W_12 sst_27N-49W_7 sst_27N-49W_8 sst_27N-49W_9 sst_27N-49W_10 sst_27N-49W_11 sst_27N-49W_12 sst_27N-47W_7 sst_27N-47W_8 sst_27N-47W_9 sst_27N-47W_10 sst_27N-47W_11 sst_27N-47W_12 sst_27N-45W_7 sst_27N-45W_8 sst_27N-45W_9 sst_27N-45W_10 sst_27N-45W_11 sst_27N-45W_12 sst_27N-43W_7 sst_27N-43W_8 sst_27N-43W_9 sst_27N-43W_10 sst_27N-43W_11 sst_27N-43W_12 sst_27N-41W_7 sst_27N-41W_8 sst_27N-41W_9 sst_27N-41W_10 sst_27N-41W_11 sst_27N-41W_12 sst_27N-39W_7 sst_27N-39W_8 sst_27N-39W_9 sst_27N-39W_10 sst_27N-39W_11 sst_27N-39W_12 sst_27N-37W_7 sst_27N-37W_8  \
1973      0.924658      0.955479      0.972603       0.928082       0.883562        0.80137      0.920139      0.954861       0.96875       0.927083       0.881944       0.798611      0.912587      0.947552      0.961538       0.923077       0.877622       0.793706      0.908451      0.943662      0.957746       0.922535       0.876761       0.799296      0.904594      0.939929       0.95053       0.922261       0.876325        0.80212       0.90106      0.932862       0.95053       0.922261       0.876325       0.805654      0.897527      0.925795      0.946996       0.922261       0.876325       0.809187      0.901408      0.926056      0.947183       0.926056       0.883803        0.81338      0.900709      0.925532      0.950355       0.929078       0.886525       0.815603      0.893238      0.914591      0.946619       0.925267       0.882562       0.818505      0.891697      0.913357      0.945848       0.927798       0.873646       0.826715      0.886029      0.911765   
1974      0.934932       0.94863       0.94863       0.907534       0.869863       0.811644      0.930556      0.944444      0.947917        0.90625       0.868056         0.8125      0.923077      0.940559      0.944056       0.905594       0.867133       0.818182      0.919014       0.93662      0.940141       0.908451       0.866197       0.823944      0.918728      0.932862      0.939929       0.908127       0.865724       0.826855      0.922261      0.932862      0.939929       0.908127       0.865724       0.823322      0.918728      0.929329      0.936396       0.908127       0.865724       0.819788      0.911972      0.926056      0.926056       0.908451       0.869718       0.827465      0.897163      0.921986      0.911348       0.904255       0.875887       0.829787      0.879004      0.914591      0.900356       0.900356       0.879004       0.829181      0.877256      0.916968      0.898917       0.902527       0.884477       0.826715      0.878676      0.922794   
1975      0.917808      0.958904      0.969178       0.931507       0.886986       0.797945      0.916667      0.961806       0.96875       0.930556       0.885417       0.795139      0.916084      0.961538      0.965035       0.926573       0.881119       0.793706      0.922535      0.964789      0.964789       0.929577       0.883803       0.799296      0.922261      0.964664      0.957597       0.925795       0.883392       0.798587      0.925795      0.961131       0.95053       0.918728       0.879859        0.80212      0.922261      0.957597      0.943463       0.911661       0.872792        0.80212      0.919014      0.961268      0.947183       0.911972       0.873239       0.806338      0.911348      0.957447      0.950355       0.911348        0.87234       0.808511      0.907473      0.953737      0.950178       0.907473       0.868327       0.807829      0.906137      0.949458      0.956679       0.913357       0.873646       0.819495      0.908088      0.948529   
1976      0.934932       0.94863 

In [140]:
#Removing 2017 due we don't have full 2018 available
dataset_df = dataset_df.loc['1973-01-01':'2016-12-01']

In [141]:
#Train
train_df = dataset_df.loc['1973-01-01':'2000-12-01']

test_df = dataset_df.loc['2000-01-01':'2016-12-01']

#Dropt last column to be the X values
feature_cols = dataset_df.columns
feature_cols=feature_cols.drop('classes')

# Input data(X)
X = train_df.loc[:, feature_cols]

# Output data(y)
y = train_df['classes']

X_test = test_df.loc[:, feature_cols]


### Testing classifiers for tn

In [142]:
new_pred_class = test_knn(X,y)

2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 normal
2001 weak
2001 normal


In [143]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.6875

In [144]:
new_pred_class = test_svc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [145]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [146]:
new_pred_class = test_gpc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 normal
2009 weak
2010 normal
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [147]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [148]:
new_pred_class = test_dtc(X,y)

2001 strong
2002 normal
2003 weak
2004 strong
2005 weak
2006 weak
2007 strong
2008 weak
2009 strong
2010 weak
2011 weak
2012 weak
2013 weak
2014 normal
2015 normal
2016 normal


In [149]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5

In [150]:
new_pred_class = test_rfc(X,y)

2001 weak
2002 normal
2003 normal
2004 normal
2005 normal
2006 normal
2007 normal
2008 normal
2009 normal
2010 normal
2011 normal
2012 normal
2013 normal
2014 normal
2015 weak
2016 normal


In [151]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.3125

In [152]:
new_pred_class = test_mlp(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 normal
2015 normal
2016 normal


In [153]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.625

In [154]:
new_pred_class = test_adc(X,y)

2001 weak
2002 normal
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 normal
2012 weak
2013 weak
2014 normal
2015 normal
2016 normal


In [155]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.625

In [156]:
new_pred_class = test_gnb(X,y)

2001 normal
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [157]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.75

# AFTER 2


### Prepare data for TS

In [158]:
ts_sst_transformed_df = create_transformed_df(ts_sst_scaled_df, "sst_")
ts_sst_transformed_df.head()

sst_5N-51W_7 sst_5N-51W_8 sst_5N-51W_9 sst_5N-51W_10 sst_5N-51W_11 sst_5N-51W_12 sst_5N-49W_7 sst_5N-49W_8 sst_5N-49W_9 sst_5N-49W_10 sst_5N-49W_11 sst_5N-49W_12 sst_5N-47W_7 sst_5N-47W_8 sst_5N-47W_9 sst_5N-47W_10 sst_5N-47W_11 sst_5N-47W_12 sst_5N-45W_7 sst_5N-45W_8 sst_5N-45W_9 sst_5N-45W_10 sst_5N-45W_11 sst_5N-45W_12 sst_5N-43W_7 sst_5N-43W_8 sst_5N-43W_9 sst_5N-43W_10 sst_5N-43W_11 sst_5N-43W_12 sst_5N-41W_7 sst_5N-41W_8 sst_5N-41W_9 sst_5N-41W_10 sst_5N-41W_11 sst_5N-41W_12 sst_5N-39W_7 sst_5N-39W_8 sst_5N-39W_9 sst_5N-39W_10 sst_5N-39W_11 sst_5N-39W_12 sst_5N-37W_7 sst_5N-37W_8 sst_5N-37W_9 sst_5N-37W_10 sst_5N-37W_11 sst_5N-37W_12 sst_5N-35W_7 sst_5N-35W_8 sst_5N-35W_9 sst_5N-35W_10 sst_5N-35W_11 sst_5N-35W_12 sst_5N-33W_7 sst_5N-33W_8 sst_5N-33W_9 sst_5N-33W_10 sst_5N-33W_11 sst_5N-33W_12 sst_5N-31W_7 sst_5N-31W_8 sst_5N-31W_9 sst_5N-31W_10 sst_5N-31W_11 sst_5N-31W_12 sst_5N-29W_7 sst_5N-29W_8 sst_5N-29W_9 sst_5N-29W_10 sst_5N-29W_11 sst_5N-29W_12 sst_5N-27W_7  \
1973     0.942953     0.966443      0.95302      0.939597       0.95302      0.926174     0.936027     0.949495     0.956229      0.942761      0.942761      0.919192     0.939189     0.949324     0.966216      0.952703      0.939189      0.922297     0.949324     0.959459     0.976351      0.959459      0.952703      0.935811     0.955932     0.969492     0.976271      0.959322      0.955932      0.945763     0.966102     0.976271     0.979661      0.959322      0.959322      0.949153     0.969595     0.972973     0.983108      0.949324      0.949324      0.935811     0.969697      0.96633     0.976431      0.939394       0.93266      0.922559     0.959459     0.969595     0.969595      0.949324      0.939189      0.929054     0.952542     0.966102     0.959322      0.962712      0.942373      0.935593     0.952218     0.959044     0.948805      0.969283      0.952218       0.94198     0.945205     0.945205     0.941781      0.965753      0.952055      0.938356      0.94863   
1974      0.95302     0.936242     0.942953      0.932886       0.95302      0.909396     0.952862     0.925926     0.936027      0.925926      0.939394      0.909091     0.949324     0.925676     0.939189      0.929054      0.935811      0.915541     0.945946     0.932432     0.952703      0.935811      0.939189      0.918919     0.935593     0.938983     0.962712      0.942373      0.942373      0.918644     0.935593     0.938983     0.966102      0.949153      0.942373      0.922034     0.939189     0.935811     0.962838      0.952703      0.939189      0.925676     0.939394     0.925926     0.949495      0.946128       0.93266      0.929293     0.939189     0.925676     0.949324      0.942568      0.932432      0.932432     0.942373     0.922034     0.949153      0.935593      0.938983      0.928814      0.94198     0.924915     0.945392      0.938567       0.94198      0.928328     0.938356     0.921233     0.934932      0.934932      0.938356      0.924658     0.938356   
1975     0.959732     0.932886     0.912752      0.932886      0.942953      0.919463     0.949495      0.93266     0.905724      0.936027      0.929293      0.912458     0.942568     0.942568     0.915541      0.949324      0.925676      0.915541     0.945946     0.949324     0.932432      0.966216      0.935811      0.929054     0.945763     0.952542     0.949153      0.972881      0.938983      0.938983     0.949153     0.949153     0.959322      0.976271      0.935593      0.942373     0.942568     0.942568     0.966216      0.962838      0.925676      0.935811      0.93266     0.925926     0.959596      0.939394      0.909091      0.925926     0.918919     0.908784     0.942568      0.932432      0.912162      0.918919     0.911864     0.894915     0.928814      0.928814      0.915254      0.915254     0.921502     0.897611     0.918089      0.935154      0.924915      0.914676     0.928082      0.90411     0.910959      0.931507      0.924658      0.910959     0.938356   
1976     0.922819     0.932886   

In [159]:
ts_pws_transformed_df = create_transformed_df(ts_pws_scaled_df, "pws_")
ts_pws_transformed_df.head()

pws_5N-51W_7 pws_5N-51W_8 pws_5N-51W_9 pws_5N-51W_10 pws_5N-51W_11 pws_5N-51W_12 pws_5N-49W_7 pws_5N-49W_8 pws_5N-49W_9 pws_5N-49W_10 pws_5N-49W_11 pws_5N-49W_12 pws_5N-47W_7 pws_5N-47W_8 pws_5N-47W_9 pws_5N-47W_10 pws_5N-47W_11 pws_5N-47W_12 pws_5N-45W_7 pws_5N-45W_8 pws_5N-45W_9 pws_5N-45W_10 pws_5N-45W_11 pws_5N-45W_12 pws_5N-43W_7 pws_5N-43W_8 pws_5N-43W_9 pws_5N-43W_10 pws_5N-43W_11 pws_5N-43W_12 pws_5N-41W_7 pws_5N-41W_8 pws_5N-41W_9 pws_5N-41W_10 pws_5N-41W_11 pws_5N-41W_12 pws_5N-39W_7 pws_5N-39W_8 pws_5N-39W_9 pws_5N-39W_10 pws_5N-39W_11 pws_5N-39W_12 pws_5N-37W_7 pws_5N-37W_8 pws_5N-37W_9 pws_5N-37W_10 pws_5N-37W_11 pws_5N-37W_12 pws_5N-35W_7 pws_5N-35W_8 pws_5N-35W_9 pws_5N-35W_10 pws_5N-35W_11 pws_5N-35W_12 pws_5N-33W_7 pws_5N-33W_8 pws_5N-33W_9 pws_5N-33W_10 pws_5N-33W_11 pws_5N-33W_12 pws_5N-31W_7 pws_5N-31W_8 pws_5N-31W_9 pws_5N-31W_10 pws_5N-31W_11 pws_5N-31W_12 pws_5N-29W_7 pws_5N-29W_8 pws_5N-29W_9 pws_5N-29W_10 pws_5N-29W_11 pws_5N-29W_12 pws_5N-27W_7  \
1973     0.125373    0.0486267     0.131754      0.274557      0.187062      0.362308     0.103344    0.0368883     0.123748      0.250561      0.217832      0.357118    0.0744924    0.0453909    0.0967753      0.206388       0.27027      0.365294     0.106525     0.103611      0.12726      0.209937      0.365956      0.404197     0.130868     0.169764     0.211658      0.275566      0.474805       0.47209     0.113622     0.226527     0.270209      0.338411      0.541007      0.479922     0.108248     0.285375     0.286569      0.389607      0.528561      0.443155     0.117408     0.263051     0.308972      0.398711       0.53999      0.440077    0.0897857     0.139494     0.292438      0.292484      0.480164      0.381221     0.103985    0.0473735     0.239928      0.110828      0.355275      0.300438     0.115473    0.0744887     0.168658     0.0158381      0.249383      0.246061     0.136193     0.200075     0.129705     0.0416364      0.213666      0.236108     0.212733   
1974     0.129897    0.0676231     0.163533      0.334041      0.239373      0.604462     0.125512    0.0853302     0.154049      0.300298      0.278496      0.601218    0.0826715    0.0576073     0.137138      0.277707      0.346494       0.60818     0.073141    0.0470521     0.166078      0.306629      0.459453      0.632495    0.0641217     0.055745     0.225747       0.33418      0.567424      0.670712    0.0374051    0.0666166     0.243522      0.268916       0.58567      0.621579    0.0589397      0.13104     0.275662      0.181895      0.509802       0.52496     0.106082     0.237077     0.362809      0.200318      0.505252      0.536769     0.110998     0.290094     0.438965      0.219717      0.550467      0.495276     0.150469     0.346661     0.456997      0.217769      0.516877      0.402049     0.174468     0.373611     0.420928      0.175016      0.423929      0.295931     0.207725     0.403072     0.407511      0.130539      0.322847      0.208543      0.23125   
1975     0.135462     0.127024     0.188917      0.034643      0.108612      0.244766     0.073269     0.130292     0.179738     0.0719412      0.131609      0.223085            0      0.13377     0.179939     0.0993464      0.139054      0.213195   0.00679507     0.180877      0.22712      0.169951      0.180775      0.258865     0.035023     0.270084     0.308163      0.229262      0.236534      0.347504    0.0265964     0.317942     0.336344      0.208356      0.248826       0.42305    0.0321747     0.323962     0.332314      0.160091      0.256697      0.454899    0.0406315     0.357776     0.376789      0.121595      0.297305      0.471016   0.00970479     0.344022     0.381825     0.0406105      0.293653      0.411005    0.0159285     0.372258     0.378009     0.0507599      0.243323      0.285501            0     0.404087     0.357873     0.0858044      0.156781      0.189698    0.0206469     0.471412     0.337079      0.110462     0.0916336      0.147498     0.153611   
1976     0.140687    0.0248163   

In [160]:
df_new = pd.concat([ts_sst_transformed_df, ts_pws_transformed_df], axis=1)
df_new.head()


sst_5N-51W_7 sst_5N-51W_8 sst_5N-51W_9 sst_5N-51W_10 sst_5N-51W_11 sst_5N-51W_12 sst_5N-49W_7 sst_5N-49W_8 sst_5N-49W_9 sst_5N-49W_10 sst_5N-49W_11 sst_5N-49W_12 sst_5N-47W_7 sst_5N-47W_8 sst_5N-47W_9 sst_5N-47W_10 sst_5N-47W_11 sst_5N-47W_12 sst_5N-45W_7 sst_5N-45W_8 sst_5N-45W_9 sst_5N-45W_10 sst_5N-45W_11 sst_5N-45W_12 sst_5N-43W_7 sst_5N-43W_8 sst_5N-43W_9 sst_5N-43W_10 sst_5N-43W_11 sst_5N-43W_12 sst_5N-41W_7 sst_5N-41W_8 sst_5N-41W_9 sst_5N-41W_10 sst_5N-41W_11 sst_5N-41W_12 sst_5N-39W_7 sst_5N-39W_8 sst_5N-39W_9 sst_5N-39W_10 sst_5N-39W_11 sst_5N-39W_12 sst_5N-37W_7 sst_5N-37W_8 sst_5N-37W_9 sst_5N-37W_10 sst_5N-37W_11 sst_5N-37W_12 sst_5N-35W_7 sst_5N-35W_8 sst_5N-35W_9 sst_5N-35W_10 sst_5N-35W_11 sst_5N-35W_12 sst_5N-33W_7 sst_5N-33W_8 sst_5N-33W_9 sst_5N-33W_10 sst_5N-33W_11 sst_5N-33W_12 sst_5N-31W_7 sst_5N-31W_8 sst_5N-31W_9 sst_5N-31W_10 sst_5N-31W_11 sst_5N-31W_12 sst_5N-29W_7 sst_5N-29W_8 sst_5N-29W_9 sst_5N-29W_10 sst_5N-29W_11 sst_5N-29W_12 sst_5N-27W_7  \
1973     0.942953     0.966443      0.95302      0.939597       0.95302      0.926174     0.936027     0.949495     0.956229      0.942761      0.942761      0.919192     0.939189     0.949324     0.966216      0.952703      0.939189      0.922297     0.949324     0.959459     0.976351      0.959459      0.952703      0.935811     0.955932     0.969492     0.976271      0.959322      0.955932      0.945763     0.966102     0.976271     0.979661      0.959322      0.959322      0.949153     0.969595     0.972973     0.983108      0.949324      0.949324      0.935811     0.969697      0.96633     0.976431      0.939394       0.93266      0.922559     0.959459     0.969595     0.969595      0.949324      0.939189      0.929054     0.952542     0.966102     0.959322      0.962712      0.942373      0.935593     0.952218     0.959044     0.948805      0.969283      0.952218       0.94198     0.945205     0.945205     0.941781      0.965753      0.952055      0.938356      0.94863   
1974      0.95302     0.936242     0.942953      0.932886       0.95302      0.909396     0.952862     0.925926     0.936027      0.925926      0.939394      0.909091     0.949324     0.925676     0.939189      0.929054      0.935811      0.915541     0.945946     0.932432     0.952703      0.935811      0.939189      0.918919     0.935593     0.938983     0.962712      0.942373      0.942373      0.918644     0.935593     0.938983     0.966102      0.949153      0.942373      0.922034     0.939189     0.935811     0.962838      0.952703      0.939189      0.925676     0.939394     0.925926     0.949495      0.946128       0.93266      0.929293     0.939189     0.925676     0.949324      0.942568      0.932432      0.932432     0.942373     0.922034     0.949153      0.935593      0.938983      0.928814      0.94198     0.924915     0.945392      0.938567       0.94198      0.928328     0.938356     0.921233     0.934932      0.934932      0.938356      0.924658     0.938356   
1975     0.959732     0.932886     0.912752      0.932886      0.942953      0.919463     0.949495      0.93266     0.905724      0.936027      0.929293      0.912458     0.942568     0.942568     0.915541      0.949324      0.925676      0.915541     0.945946     0.949324     0.932432      0.966216      0.935811      0.929054     0.945763     0.952542     0.949153      0.972881      0.938983      0.938983     0.949153     0.949153     0.959322      0.976271      0.935593      0.942373     0.942568     0.942568     0.966216      0.962838      0.925676      0.935811      0.93266     0.925926     0.959596      0.939394      0.909091      0.925926     0.918919     0.908784     0.942568      0.932432      0.912162      0.918919     0.911864     0.894915     0.928814      0.928814      0.915254      0.915254     0.921502     0.897611     0.918089      0.935154      0.924915      0.914676     0.928082      0.90411     0.910959      0.931507      0.924658      0.910959     0.938356   
1976     0.922819     0.932886   

In [161]:
dataset_df = pd.concat([df_new, rainy_classified_df], axis=1)
dataset_df.head()

sst_5N-51W_7 sst_5N-51W_8 sst_5N-51W_9 sst_5N-51W_10 sst_5N-51W_11 sst_5N-51W_12 sst_5N-49W_7 sst_5N-49W_8 sst_5N-49W_9 sst_5N-49W_10 sst_5N-49W_11 sst_5N-49W_12 sst_5N-47W_7 sst_5N-47W_8 sst_5N-47W_9 sst_5N-47W_10 sst_5N-47W_11 sst_5N-47W_12 sst_5N-45W_7 sst_5N-45W_8 sst_5N-45W_9 sst_5N-45W_10 sst_5N-45W_11 sst_5N-45W_12 sst_5N-43W_7 sst_5N-43W_8 sst_5N-43W_9 sst_5N-43W_10 sst_5N-43W_11 sst_5N-43W_12 sst_5N-41W_7 sst_5N-41W_8 sst_5N-41W_9 sst_5N-41W_10 sst_5N-41W_11 sst_5N-41W_12 sst_5N-39W_7 sst_5N-39W_8 sst_5N-39W_9 sst_5N-39W_10 sst_5N-39W_11 sst_5N-39W_12 sst_5N-37W_7 sst_5N-37W_8 sst_5N-37W_9 sst_5N-37W_10 sst_5N-37W_11 sst_5N-37W_12 sst_5N-35W_7 sst_5N-35W_8 sst_5N-35W_9 sst_5N-35W_10 sst_5N-35W_11 sst_5N-35W_12 sst_5N-33W_7 sst_5N-33W_8 sst_5N-33W_9 sst_5N-33W_10 sst_5N-33W_11 sst_5N-33W_12 sst_5N-31W_7 sst_5N-31W_8 sst_5N-31W_9 sst_5N-31W_10 sst_5N-31W_11 sst_5N-31W_12 sst_5N-29W_7 sst_5N-29W_8 sst_5N-29W_9 sst_5N-29W_10 sst_5N-29W_11 sst_5N-29W_12 sst_5N-27W_7  \
1973     0.942953     0.966443      0.95302      0.939597       0.95302      0.926174     0.936027     0.949495     0.956229      0.942761      0.942761      0.919192     0.939189     0.949324     0.966216      0.952703      0.939189      0.922297     0.949324     0.959459     0.976351      0.959459      0.952703      0.935811     0.955932     0.969492     0.976271      0.959322      0.955932      0.945763     0.966102     0.976271     0.979661      0.959322      0.959322      0.949153     0.969595     0.972973     0.983108      0.949324      0.949324      0.935811     0.969697      0.96633     0.976431      0.939394       0.93266      0.922559     0.959459     0.969595     0.969595      0.949324      0.939189      0.929054     0.952542     0.966102     0.959322      0.962712      0.942373      0.935593     0.952218     0.959044     0.948805      0.969283      0.952218       0.94198     0.945205     0.945205     0.941781      0.965753      0.952055      0.938356      0.94863   
1974      0.95302     0.936242     0.942953      0.932886       0.95302      0.909396     0.952862     0.925926     0.936027      0.925926      0.939394      0.909091     0.949324     0.925676     0.939189      0.929054      0.935811      0.915541     0.945946     0.932432     0.952703      0.935811      0.939189      0.918919     0.935593     0.938983     0.962712      0.942373      0.942373      0.918644     0.935593     0.938983     0.966102      0.949153      0.942373      0.922034     0.939189     0.935811     0.962838      0.952703      0.939189      0.925676     0.939394     0.925926     0.949495      0.946128       0.93266      0.929293     0.939189     0.925676     0.949324      0.942568      0.932432      0.932432     0.942373     0.922034     0.949153      0.935593      0.938983      0.928814      0.94198     0.924915     0.945392      0.938567       0.94198      0.928328     0.938356     0.921233     0.934932      0.934932      0.938356      0.924658     0.938356   
1975     0.959732     0.932886     0.912752      0.932886      0.942953      0.919463     0.949495      0.93266     0.905724      0.936027      0.929293      0.912458     0.942568     0.942568     0.915541      0.949324      0.925676      0.915541     0.945946     0.949324     0.932432      0.966216      0.935811      0.929054     0.945763     0.952542     0.949153      0.972881      0.938983      0.938983     0.949153     0.949153     0.959322      0.976271      0.935593      0.942373     0.942568     0.942568     0.966216      0.962838      0.925676      0.935811      0.93266     0.925926     0.959596      0.939394      0.909091      0.925926     0.918919     0.908784     0.942568      0.932432      0.912162      0.918919     0.911864     0.894915     0.928814      0.928814      0.915254      0.915254     0.921502     0.897611     0.918089      0.935154      0.924915      0.914676     0.928082      0.90411     0.910959      0.931507      0.924658      0.910959     0.938356   
1976     0.922819     0.932886   

In [162]:
#Removing 2017 due we don't have full 2018 available
dataset_df = dataset_df.loc['1973-01-01':'2016-12-01']

In [163]:
#Train
train_df = dataset_df.loc['1973-01-01':'2000-12-01']

test_df = dataset_df.loc['2000-01-01':'2016-12-01']

#Dropt last column to be the X values
feature_cols = dataset_df.columns
feature_cols=feature_cols.drop('classes')

# Input data(X)
X = train_df.loc[:, feature_cols]

# Output data(y)
y = train_df['classes']

X_test = test_df.loc[:, feature_cols]


### Testing classifiers for ats

In [164]:
new_pred_class = test_knn(X,y)

2001 normal
2001 normal
2001 normal
2001 normal
2001 weak
2001 weak
2001 normal
2001 normal
2001 normal
2001 normal
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak
2001 weak


In [165]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.6875

In [166]:
new_pred_class = test_svc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [167]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.8125

In [168]:
new_pred_class = test_gpc(X,y)

2001 normal
2002 normal
2003 normal
2004 normal
2005 weak
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [169]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.6875

In [170]:
new_pred_class = test_dtc(X,y)

2001 weak
2002 strong
2003 weak
2004 normal
2005 normal
2006 weak
2007 weak
2008 weak
2009 weak
2010 weak
2011 weak
2012 normal
2013 weak
2014 weak
2015 weak
2016 weak


In [171]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.625

In [172]:
new_pred_class = test_rfc(X,y)

2001 normal
2002 normal
2003 normal
2004 normal
2005 weak
2006 normal
2007 normal
2008 normal
2009 normal
2010 normal
2011 weak
2012 normal
2013 normal
2014 normal
2015 weak
2016 normal


In [173]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.375

In [174]:
new_pred_class = test_mlp(X,y)

2001 normal
2002 normal
2003 normal
2004 normal
2005 normal
2006 normal
2007 normal
2008 normal
2009 normal
2010 normal
2011 normal
2012 normal
2013 normal
2014 normal
2015 normal
2016 normal


In [175]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.1875

In [176]:
new_pred_class = test_adc(X,y)

2001 weak
2002 weak
2003 weak
2004 weak
2005 weak
2006 weak
2007 weak
2008 weak
2009 normal
2010 weak
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [177]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.75

In [178]:
new_pred_class = test_gnb(X,y)

2001 weak
2002 weak
2003 normal
2004 normal
2005 weak
2006 normal
2007 weak
2008 weak
2009 normal
2010 normal
2011 weak
2012 weak
2013 weak
2014 weak
2015 weak
2016 weak


In [179]:
metrics.accuracy_score(test_df['classes'], new_pred_class)

0.5